# Дипломная работа по NLP

«Создание аналитической информационной системы для выделения ключевых слов из учебных материалов»

## Выполнил: студент группы ПИ20-5, Валяев Георгий Анатольевич

В этом скрипте будут реализованы процессы:
- загрузки датасета файлов РПД
- промежуточной аналитики данных
- создания парсера ключевых разделов РПД
- оформления итоговой структуры данных для работы скрипта `NLP_model_Valyaev.ipynb`

**Все изменения и версии ноутбуков хранятся на репозитории GitHub:
https://github.com/Valyaevgeorgiy/VKR_work**

Полезные материалы и литература к работе:
- https://neurohive.io/ru/osnovy-data-science/7-arhitektur-nejronnyh-setej-nlp/
- https://neurohive.io/ru/papers/depth-estimation-using-encoder-decoder-networks-and-self-supervised-learning/
- https://nlp.stanford.edu/courses/cs224n/2011/reports/ehhuang.pdf

In [98]:
!pip install python-docx

In [99]:
import os, re, json, traceback
import pandas as pd
from google.colab import drive

# модуль для работы с вордовскими документами и их содержимым (тексты, таблицы)
import docx

In [100]:
PATH = '/content/gdrive/MyDrive/Диплом_Валяев/dataset'

docs_2020_path = PATH+'/2020_year/'
docs_2021_path = PATH+'/2021_year/'
docs_2022_path = PATH+'/2022_year/'
docs_2023_path = PATH+'/2023_year/'
docs_engl = PATH+'/Англ РПД/'
docs_others = PATH+'/ГИА, практика и т.п./'

links_docs = '/content/gdrive/MyDrive/Диплом_Валяев/data/gd-discips-links.json'

drive.mount('/content/gdrive', force_remount=True)

Mounted at /content/gdrive


## Обработка учебных материалов

### Сбор текстовых данных РПД

#### 2020-2023 года

In [102]:
files_2020 = os.listdir(docs_2020_path)
files_2021 = os.listdir(docs_2021_path)
files_2022 = os.listdir(docs_2022_path)
files_2023 = os.listdir(docs_2023_path)

print("РПД 2020 года:\n")
for file in files_2020:
  print(file)

print()
print()

print("РПД 2021 года:\n")
for file in files_2021:
  print(file)

print()
print()

print("РПД 2022 года:\n")
for file in files_2022:
  print(file)

print()
print()

print("РПД 2023 года:\n")
for file in files_2023:
  print(file)

РПД 2020 года:

Прикл задачи МОиОБД, Эк, КФУ.docx
Методы ВД,Эк,КФУ.docx
Програм. на языках PYTHON и SQL,Эк, КФУ.docx
Нейронные сети,Эк, КФУ.docx
Обработка данных и мод. в МЕ,Эк, КФУ.docx


РПД 2021 года:

Инт вещей, ПИ, 2021.docx
Агент мод.docx
Интел тех в УР.docx
Соврем НТ, 2021.docx
Бухгалтерские ИС.docx
Диф урав.docx
Метод ПИДиПДДА.docx
АС БУ АиА в КО.docx
Прогр на яз Python и SQL, Эк.docx
СоврТП, ПИ.docx
Прогр и АД с пом PYTHON, Ин.docx
Реком системы.docx
Прикл задачи МОиОБД, Эк.docx
Прикл мод и МТСС.docx
А-О мод, (ПИ, з, 2021).docx
Алгоритмы и ТАСС.docx
Прикл мод и МФДиКА.docx
Блокчейн-платформы.docx
Информ СЭА.docx
Методы ВД,.docx
Прикл модели и МРА.docx
Введение в НоД, ПМИ.docx
Диск мат, ИБ.docx
Введение в спец., ПМИ.docx
Инстр-ые средства СФ, Эк, ФТБ.docx
Геоинформ. системы.docx
Введение в спец., ПИ.docx
Нереляционные БД, ПИ.DOCX
Построение и ОММО, ПМИ.docx
Сетевые СиП.docx
Основы ЦиРАК.docx
Аналит ИТиС, Эк.docx
Основы МОЕЯ (NLP).DOCX
Автоматизированные БСиДБС, ПИ.docx
Интер

#### ГИА, практики и English РПД

In [103]:
files_others = os.listdir(docs_others)
files_engl = os.listdir(docs_engl)

print("Файлы практик, ГИА:\n")
for file in files_others:
  print(file)

print()
print()

print("РПД на английском языке:\n")
for file in files_engl:
  print(file)

Файлы практик, ГИА:

НИС, ПИ (з).docx
Пед практика, Эк, 2021.docx
НИР, ПИ (з).docx
Прогр КЭ по МиИМЭ, Эк, 2021.docx
ГИА, ПИ, 19, 20.docx
ГИА ПМИ, 2020.docx
ГИА, МиИМЭ, 2021.docx
Пед пр, МСиИМвЭ, 2022.docx
Пед практика, 2022.docx
ГИА, ПМИ, 2019.docx
ГИА, ПИ, 2019.docx
ГИА,ПИ,ОБД,2021.docx
ГИА, АБД,2021.docx
Прогр КЭ - ММЧМиКП, ИВТ, 2022.docx
НИС (КЗ, 2022).docx
НИС, Мех, 2022.docx
НИР (ПМО,2022).docx
Прогр КЭ по МСиИМвЭ, 2022.docx
НИР, Мех, 2022.docx
НИС (ИАТиСС, 2022).docx
НИС (ПУОРИС, 2022).docx
НИР (ИАТиСС, 2022).docx
НИР (ПУОРИС,2022).docx
НИС, УБД, 2022.docx
НИР (КЗ, 2022).docx
НИР (УБД, 2022).docx
Уч. практика, КЗ, 2022.docx
НИР (ИТвАПК, 2022).docx
НМС, ИВТ, 2022.docx
НИРС,ПМО,  2023.docx
Пр практика, ВВвЦЭ, 2021.docx
Уч практика, ПМО, 2022.docx
НИРС, ПИС, ИОО, з, 2022.docx
ГИА, ВВ в ЦЭ, 2021.docx
Уч практика, ВВвЦЭ, 2021.docx
Уч практика, ИТ-С, 2021.docx
Пр практика, ПМО, 2022.docx
Пр практика, ИТ-С, 2021.docx
Пр практика, КЗ.docx
Пр практика, АД, 2021.docx
Уч практика, ИАТ,  202

### Сбор ссылок на документы

Полезная статья для получения данных с Google Drive: https://www.datalytics.ru/all/rabotaem-s-api-google-drive-s-pomoschyu-python/

In [104]:
with open(links_docs, 'r', encoding='utf-8') as file_l:
  rpd_links = json.load(file_l)

dict(list(rpd_links.items())[:5])

{'MLOps, 2022.docx': 'vk.cc/cvqvs7',
 'NoSQL СУБД, 2022.docx': 'vk.cc/cvqyPy',
 'Web-программ, Мен, 2023.docx': 'vk.cc/cvqvfY',
 'Web-программ, ПИ, 2023.docx': 'vk.cc/cvqvfU',
 'А и СД в яз Python, БИ, 2023.docx': 'vk.cc/cvqvf7'}

In [105]:
# решение кейса, когда названия файлов, взятые через os и через google service account, не совпадают, но по наполнению идентичные
files_d = list(rpd_links.keys())
os_files = sorted(files_2020 + files_2021 + files_2022 + files_2023)
for file_d, os_file in zip(files_d, os_files):
  if file_d != os_file:
    link = rpd_links[file_d]
    del rpd_links[file_d]

    rpd_links[os_file] = link

In [106]:
assert sorted(list(rpd_links.keys())) == os_files

### Предобработка данных

#### Класс предобработчика

In [125]:
class DatasetPreprocessor:

  def screen_docx_file(self, docs_path, files_path):
    """
    Показ титульников РПД и её краткой сводки.
    return: str/None
    """
    count_files = len(files_path) if (len(files_path)) <= 10 else 10
    for ind in range(count_files):
      doc = docx.Document(docs_path + files_path[ind])
      text_paragraphs = [p.text.lower().strip() for p in doc.paragraphs if p.text != '']
      print(f'Документ № {ind+1}')
      print(f'Название документа => {files_path[ind]}')
      print(f"Количество строк — {len(doc.paragraphs)}")
      print(*text_paragraphs[:10], sep='\n')
      print()
      print()
    if len(files_path) > 10:
      return "......"


  def get_analytic_data_rpds(self):
    """
    Количественная аналитика датасета.
    return: None
    """
    print(f"2020 год — {len(files_2020)}")
    print(f"2021 год — {len(files_2021)}")
    print(f"2022 год — {len(files_2022)}")
    print(f"2023 год — {len(files_2023)}")
    print()
    print(f"Итоговое количество РПД (после очистки .doc) в рамках датасета = {len(files_2020) + len(files_2021) + len(files_2022) + len(files_2023)}")
    print(f"Количество документов по практике, ГИА и т.п. в рамках датасета = {len(files_engl) + len(files_others)}")


  def search_index_by_string(self, string_list, keyword):
    """
    Поиск индексов в списке строк по описанию раздела РПД.
    return: list
    """
    lst_keywords = []
    matched_strings = list(filter(lambda x: keyword in x, string_list))
    if keyword == "вопросы для подготовки к зачету" and matched_strings == []:
      lst_keywords = ["вопросов для подготовки к зачету", "вопросов для подготовки к зачетам",
                      "вопросы для подготовки к экзамену", "вопросы для подготовки к экзаменам",
                      "вопросы для подготовки к кандидатскому экзамену",
                      "вопросов для подготовки к сдаче кандидатского экзамена"]

    elif keyword == "текущему контролю)))" and matched_strings == []:
      lst_keywords = ["вопросы к контрольным работам", "вопросов к контрольным работам",
                      "вопросы к контрольной работе", "вопросы для дискуссий",
                      "тематика для дискуссий", "вопросы для обсуждения на семинарских занятиях"]

    for kwd in lst_keywords:
      matched_strings = list(filter(lambda x: kwd in x, string_list))
      if matched_strings != []:
        break

    return [string_list.index(word) for word in matched_strings]


  def search_index_by_table(self, tables_list, keyword):
    """
    Поиск индексов в таблицах РПД на
    тематику вопросов для изучения к семинарам.
    return: list
    """
    stop_rows = ['наименование тем (разделов) дисциплины', 'в целом по дисциплине', 'итого в %',
                'наименование темы (разделов) дисциплины', 'наименование темы (раздела) дисциплины',
                'наименование тем  (разделов) дисциплины', 'наименование тем (разделов)  дисциплины',
                '', 'наименование тем   (разделов) дисциплины', 'в целом по  дисциплине', 'итого',
                'итого:', '1 семестр', '2 семестр', '3 семестр', 'дисциплины', 'наименование тем (разделов)', 'итого в %:',
                'введение', 'всего по дисциплине', 'наименование тем (разделов) дисциплины',
                '5 семестр', '6 семестр', 'итог в %', 'итого, в %', 'итого в часах', 'итогов %']
    for table in tables_list:
      if len(table[0]) > 1 and table[0][1].startswith(keyword):
        # for row in table:
        #   print(row)
        #   print(len(row))
        #   print()
        if keyword.startswith('наименование тем'):
          themes_list = [row[1].replace('.', '').replace('\n', ' ') for row in table if (row[1].strip().replace('.', '').replace('\n', ' ') not in stop_rows)]
          return [' '.join([elem for elem in theme.split() if (elem != '') and (elem.isdigit() == False) and (elem != 'тема')]).capitalize() for theme in themes_list if ' '.join([elem for elem in theme.split() if elem != '']) not in stop_rows and 'раздел' not in ' '.join([elem for elem in theme.split() if elem != ''])]
        else:
          return [row[1] for row in table][1:]

      elif len(table[0]) > 1 and table[0][0].startswith(keyword):
        themes_list = [row[0].replace('.', '').replace('\n', ' ') for row in table if (row[0].strip().replace('.', '').replace('\n', ' ') not in stop_rows)]
        return [' '.join([elem for elem in theme.split() if (elem != '') and (elem.isdigit() == False) and (elem != 'тема')]).capitalize() for theme in themes_list if ' '.join([elem for elem in theme.split() if elem != '']) not in stop_rows and 'раздел' not in ' '.join([elem for elem in theme.split() if elem != ''])]


  def get_themes_rpd(self, doc_path):
    """
    Выделение тематического плана дисциплины.
    return: list
    """
    doc = docx.Document(doc_path)
    tables = [[[cell.text.lower().strip() for cell in row.cells] for row in t.rows] for t in doc.tables]
    return self.search_index_by_table(tables, 'наименование тем')


  def dopparse(self, strok):
    """
    Дополнительный парсинг, который позволяет выявить в данных отдельные
    кейсы и фиксировать ключевые разделы документа.
    return: str
    """
    if '5.1.' in strok or strok == 'содержание дисциплины' or strok == '5.1 содержание дисциплины':
      strok += ')))'
    elif '5.2' in strok or strok == 'учебно тематический план' or strok == '5.2 учебно тематический план' or strok == '. учебно тематический план' or strok == 'учебно – тематический план' or strok == '. учебно – тематический план':
      strok += ')))'
    elif '6.2' in strok or strok == 'перечень вопросов, заданий, тем для подготовки к текущему контролю' or strok == '6.2 перечень вопросов, заданий, тем для подготовки к текущему контролю' or strok == '. перечень вопросов, заданий, тем для подготовки к текущему контролю':
      strok += ')))'
    elif "«" in strok or '»' in strok:
      strok = strok.replace('«', '').replace('»', '')
    return strok


  def parse_rpd_doc(self, doc_path, file_name, str_output=True):
    """
    Парсинг документов РПД
    return: str/tuple
    """
    doc = docx.Document(doc_path)

    # выделение табличной и текстовой части документа
    text_paragraphs = [self.dopparse(' '.join(p.text.lower().strip().replace('ё', 'е').replace('\n', ' ').replace('\t', ' ').split('-'))) for p in doc.paragraphs if p.text != '']
    tables = [[[cell.text.lower().strip() for cell in row.cells] for row in t.rows] for t in doc.tables]

    # наименование дисциплины
    name_discip = ''

    idx_name = self.search_index_by_string(text_paragraphs, "наименование дисциплины")
    if idx_name != []:
      idx_name = idx_name[-1] + 1
      idx_discip = idx_name + 1
      name_discip += text_paragraphs[idx_name:idx_discip][-1].replace('«', '').replace('»', '')

    # содержание дисциплины — раздел 5.1
    main_info_discip = ''

    idx_soderz_start = self.search_index_by_string(text_paragraphs, "дисциплины)))")[-1] + 1
    idx_soderz_end = self.search_index_by_string(text_paragraphs, "план)))")
    if idx_soderz_end != []:
      idx_soderz_end = idx_soderz_end[-1]
      main_info_discip = text_paragraphs[idx_soderz_start:idx_soderz_end]

    # примерные вопросы к контрольной работе — раздел 6.2
    ques_control_discip = ''

    idx_control_start = self.search_index_by_string(text_paragraphs, "текущему контролю)))")
    if idx_control_start == []:
      idx_control_start = ''
      ques_control_discip = ['']
    else:
      idx_control_start = idx_control_start[-1]
      if 'контрол' not in text_paragraphs[idx_control_start+1]:
        ques_control_discip = text_paragraphs[idx_control_start+1:idx_control_start+100]
      else:
        ques_control_discip = text_paragraphs[idx_control_start+2:idx_control_start+100]

    # примерные вопросы для подготовки к зачёту/экзамену
    ques_session_discip = ''

    idx_session_start = self.search_index_by_string(text_paragraphs, "вопросы для подготовки к зачету")
    if idx_session_start == []:
      idx_session_start = ''
      ques_session_discip = ['']
    else:
      idx_session_start = idx_session_start[-1]
      ques_session_discip = text_paragraphs[idx_session_start+1:idx_session_start+100]

    # вопросы для обсуждения на семинарских, практических занятиях
    ques_seminars_discip = self.search_index_by_table(tables, 'перечень вопросов для обсуждения на семинар')

    # ссылка на документ дисциплины
    link_discip = rpd_links[file_name]

    # формат вывода данных
    if str_output:
      return f'Наименование:\n{name_discip}', f'Содержание:\n{main_info_discip}', f'Вопросы к кр:\n{ques_control_discip}', f'Вопросы к зачёту/экзамену:\n{ques_session_discip}', f'Вопросы для семинаров:\n{ques_seminars_discip}'
    else:
      return name_discip, main_info_discip, ques_control_discip, ques_session_discip, ques_seminars_discip, link_discip


  def parsing_all_docs_year(self, docs_path, files_path, year):
    """
    Парсинг РПД по конкретному году.
    return: tuple
    """
    rpd_year, names_files_rpd_year, files_rpd_names_year = dict(), dict(), dict()
    counter_rep = 0
    for i in range(len(files_path)):
      rpd_data = self.parse_rpd_doc(docs_path + files_path[i], files_path[i], str_output=False)
      themes = self.get_themes_rpd(docs_path + files_path[i])

      # здесь важно помнить, что РПД одной дисциплины со всех направлений грубо говоря
      # образуется в самое первое упоминание дисциплины в папке года РПДшек
      # при этом не учитываются данные РПД этой же дисциплины, но другого направления

      name = str(rpd_data[0].replace(".", ""))

      if name in rpd_year.keys():
        counter_rep += 1
        print("Есть совпадение!!!")
        print(f'{i+1} Документ повторяющегося РПД — {files_path[i]}')
        print(f'Название повторяющейся дисциплины — {name}')
      else:
        print(f'{i+1}) Документ РПД — {files_path[i]}:')
        print(f'Название дисциплины — {name}')

      name_disc_modify = name + f' {year}'
      rpd_year[name_disc_modify] = rpd_data[1:]
      names_files_rpd_year[name_disc_modify] = files_path[i]
      files_rpd_names_year[files_path[i]] = dict()
      files_rpd_names_year[files_path[i]]['NAME'] = name.capitalize()
      files_rpd_names_year[files_path[i]]['THEMES'] = themes
      files_rpd_names_year[files_path[i]]['LINKDOC'] = rpd_data[-1]
      print()
      print('OK!')
      print()
      print()

    print()
    print(f'ИТОГО количество повторений = {counter_rep}')
    print(f'Словарь наименований РПД и файлов датасета 2020:\n{names_files_rpd_year}')
    print(f'Словарь файлов со ссылкой на название РПД 2020:\n{files_rpd_names_year}')
    print()
    return rpd_year, names_files_rpd_year, files_rpd_names_year


  def clearing_data_punkt(self, data):
    """
    Очистка датасета от пунктуации и прочих других символов.
    return: dict
    """
    discs, prepro_data = data.keys(), dict()
    for index, disc in enumerate(discs):
      print(f'{index+1}) {disc}')

      # 1. обработка данных содержания дисциплины
      soderz = [re.sub('[^A-Za-zА-Яа-я]+', ' ', soderz_).strip() for soderz_ in data[disc][0] if re.sub('[^A-Za-zА-Яа-я]+', ' ', soderz_).strip() != '']

      # 2. обработка данных вопросов к кр
      cr_ques = [re.sub('[^A-Za-zА-Яа-я]+', ' ', cr_ques_).strip() for cr_ques_ in data[disc][1] if re.sub('[^A-Za-zА-Яа-я]+', ' ', cr_ques_).strip() != '']
      # print(cr_ques)
      if cr_ques != ['']:
        lst_keywords = ['пример задания контрольной работы', 'примеры заданий для контрольной работы',
                        'примеры заданий контрольной работы', 'примеры заданий для контрольной работы семестр',
                        'примерные задания контрольной работы модуль', 'примеры тестовых заданий',
                        'примерные задания контрольной работы',
                        'пример системы для контрольной работы',
                        'перечень основной и дополнительной учебной литературы необходимой для освоения дисциплины',
                        'критерии бальной оценки различных форм текущего контроля',
                        'критерии бальной оценки различных форм текущего контроля успеваемости',
                        'критерии балльной оценки различных форм текущего контроля',
                        'критерии балльной оценки различных форм текущего контроля успеваемости',
                        'критерии бальной оценки различных форм текущего контроля успеваемости содержатся в соответствующих методических рекомендациях департамента анализа данных и машинного обучения',
                        'критерии балльной оценки различных форм текущего контроля успеваемости содержатся в соответствующих методических рекомендациях департамента анализа данных и машинного обучения факультета информационных технологий и анализа больших данных',
                        'критерии балльной оценки различных форм текущего контроля успеваемости содержатся в соответствующих методических рекомендациях департамента анализа данных и машинного обучения',
                        'критерии бальной оценки различных форм текущего контроля успеваемости содержатся в соответствующих методических рекомендациях департамента анализа данных и машинного обучения факультета информационных технологий и анализа больших данных']
        counter_iss = 0
        for keyword in lst_keywords:
          if keyword in cr_ques:
            end_cr = cr_ques.index(keyword)
            break
          else:
            counter_iss += 1

        if counter_iss == len(lst_keywords):
          print("EMPTYYYYYYYYYYYYYYYYYYYYYY CONTROOOOLLLL")
          cr_ques = ['']

        cr_ques = cr_ques[:end_cr]

      # 3. обработка данных вопросов к зачёту/экзу
      zach_ques = [re.sub('[^A-Za-zА-Яа-я]+', ' ', zach_ques_).strip() for zach_ques_ in data[disc][2] if re.sub('[^A-Za-zА-Яа-я]+', ' ', zach_ques_).strip() != '']
      if 'перечень основной и дополнительной учебной литературы необходимой для освоения дисциплины' in zach_ques:
        end_zach = zach_ques.index('перечень основной и дополнительной учебной литературы необходимой для освоения дисциплины')
      zach_ques = zach_ques[:end_zach]

      # 4. обработка данных вопросов для семинаров
      sem_ques = [sem_ques_.strip() for sem_ques_ in data[disc][3]]
      # print(sem_ques)
      # sem_ques = [re.sub('[^A-Za-zА-Яа-я]+', ' ', zach_ques_).strip() for zach_ques_ in data[disc][3]]
      sem_now_ques = []
      for q in sem_ques:
        # print()
        # print(q)
        q = q.split('\n')
        for ind, que in enumerate(q):
          if 'рекомендуемые источники' in q[ind]:
            end_ind = ind
            break
          else:
            q[ind] = que.strip()

        # q = [que.strip() for que in q.split('\n')]
        # q = [re.sub('[^A-Za-zА-Яа-я]+', ' ', ques).strip() for ques in q.split('\n')]
        # print()
        # print(q)
        # end_ind = q.index('рекомендуемые источники:')
        sem_now_ques += [re.sub('[^A-Za-zА-Яа-я]+', ' ', ques).strip() for ques in q[:end_ind] if re.sub('[^A-Za-zА-Яа-я]+', ' ', ques).strip() != '']

      prepro_data[disc] = {'SODERZ': soderz, 'QUESKR': cr_ques, 'QUESSESS': zach_ques, 'QUESSEMS': list(set(sem_now_ques)), 'DOCLINK': data[disc][4]}

      if prepro_data[disc]['QUESKR'] == ['']:
        del prepro_data[disc]['QUESKR']

      print("OK!")
      print()
      print()

    return prepro_data


  def get_tituls_rpd(self, docs_path, files_path, year):
    """
    Парсинг титульных страниц РПД на предмет
    выявления направления подготовки.
    return: list
    """
    tituls_year = []

    print(f"Титульные страницы РПД {year} года:")
    print()
    for ind, docum in enumerate(files_path):
      doc = docx.Document(docs_path + docum)
      print()
      print(f'{ind+1}) Документ — {docum}')
      print()
      print(*[p.text.lower().strip().replace('-', ' ').replace('\n', ' ').replace('\t', ' ') for p in doc.paragraphs[6:30] if p.text != '' and p.text != ' '], sep='\n')

      titul = [p.text.lower().strip().replace('-', ' ').replace('\n', ' ').replace('\t', ' ') for p in doc.paragraphs[6:30] if p.text != '' and p.text != ' ']
      titul = [data for data in titul if ((len(data) > 0 and data[0].isdigit()) or (data.startswith('по направлению')) or (data.startswith('для студентов, обучающихся по направлению подготовки ')) or (data.startswith('дисциплина «технологии математического моделирования и анализа данных')))]
      titul = ' '.join(titul).strip().replace('«', '').replace('»', '').replace(',', '').replace('–', '').replace('\t', '').split()
      end_ind = len(titul)

      for ind, data in enumerate(titul):
        if data.count('.', 2) and len(data) == 8:
          key_ind = ind
        elif data == 'оп' or data.startswith('направленность') or data.startswith('1.'):
          end_ind = ind
      titul = [titul[key_ind:end_ind][0], ' '.join(titul[key_ind:end_ind][1:])]

      print()
      print('======================')
      print(titul)
      print('======================')
      print()
      tituls_year.append({docum: titul})

    return tituls_year


  def agg_count_napravs_year(self, tituls_data):
    """
    Агрегация числа РПД по направлениям относительно года.
    return: dict
    """
    count_napravs_year = {napr: [0, []] for napr in set([list(titul.values())[0][1] for titul in tituls_data])}
    for titul in tituls_data:
      count_napravs_year[list(titul.values())[0][1]][0] += 1
      count_napravs_year[list(titul.values())[0][1]][1].append(list(titul.keys())[0])
    count_napravs_year = {napr: [count, sorted(f)] for napr, (count, f) in count_napravs_year.items()}
    return count_napravs_year

preprocessor = DatasetPreprocessor()
preprocessor

#### Скрининг датасета

##### Скрининг ГИА, практики и English РПД

In [120]:
print(f'{len(files_engl) + len(files_others)} документов\n')

print("1) English РПД:")
print(preprocessor.screen_docx_file(docs_engl, files_engl))

print("\n2) Документы практики и ГИА:")
print(preprocessor.screen_docx_file(docs_others, files_others))

76 документов

1) English РПД:
Документ № 1
Название документа => Syllabys П и АД с пом Python, Мен,  2021, 2022.docx
Количество строк — 252
federal state educational
budgetary institution of higher education

«financial university
under the government of the russian federation »
(финансовый университет)
department of data analysis and machine learning
faculty of information technologies and big data analysis
smirnov m. v.
programming and data analysis in python (in english)
syllabus
level of study: bachelor’s degree

field of study: 38.03.02-management
op «business administration», op «business administration / bachelor of business administration (вва)», op «financial management», op «financial management / «bachelor of business administration in finance»
syllabus
name of a subject    programming and data analysis in python (in english)


Документ № 2
Название документа => Syllabys Предиктивная АБД (на англ яз).docx
Количество строк — 190
federal state educational
budgetary institutio

##### Скрининг РПД 2020-2023

In [121]:
print(f'{len(files_2020) + len(files_2021) + len(files_2022) + len(files_2023)} документов\n')

print("1) 2020 год:")
print(preprocessor.screen_docx_file(docs_2020_path, files_2020))

print("\n2) 2021 год:")
print(preprocessor.screen_docx_file(docs_2021_path, files_2021))

print("\n3) 2022 год:")
print(preprocessor.screen_docx_file(docs_2022_path, files_2022))

print("\n4) 2023 год:")
print(preprocessor.screen_docx_file(docs_2023_path, files_2023))

406 документов

1) 2020 год:
Документ № 1
Название документа => Прикл задачи МОиОБД, Эк, КФУ.docx
Количество строк — 251
федеральное государственное образовательное
бюджетное учреждение высшего образования
«финансовый университет при
правительстве российской федерации»
(финансовый университет)
департамент анализа данных и машинного обучения
факультета информационных технологий и анализа больших данных
никитин п.в., соловьев в.и.
прикладные задачи машинного обучения и обработки больших данных
рабочая программа дисциплины


Документ № 2
Название документа => Методы ВД,Эк,КФУ.docx
Количество строк — 234
федеральное государственное образовательное
бюджетное учреждение высшего образования
«финансовый университет при
правительстве российской федерации»
(финансовый университет)
департамент анализа данных и машинного обучения
факультета информационных технологий и анализа больших данных
никитин п.в., соловьев в.и.
методы визуализации данных
рабочая программа дисциплины


Документ № 3
Название 

##### Количественная аналитика датасета

In [122]:
preprocessor.get_analytic_data_rpds()

2020 год — 5
2021 год — 89
2022 год — 129
2023 год — 183

Итоговое количество РПД (после очистки .doc) в рамках датасета = 406
Количество документов по практике, ГИА и т.п. в рамках датасета = 76


#### 1 стадия предобработки

##### Будущий результат обработки

In [123]:
doc = docx.Document(docs_2020_path + files_2020[0])

#102-104 — Наименование дисциплины
#118-127 — Содержание дисциплины
#138-153 — Вопросы к контрольной работе
#173-200 — Вопросы к зачёту/экзамену

# doc.tables[3].rows
# Перечень вопросов для обсуждения на семинарских, практических занятиях, рекомендуемые источники из разделов 8,9 (указывается раздел и порядковый номер источника)

# Весь текст РПД
# text = ''
# for parag in doc.paragraphs:
  # text += parag.text + "\n"
# print(text)

print("----------------------------------- Наименование дисциплины -----------------------------------")
print()
print(*[p.text for p in doc.paragraphs[102:104]], sep="\n")
print()
print("----------------------------------- Содержание дисциплины -----------------------------------")
print()
print(*[p.text for p in doc.paragraphs[118:127]], sep="\n")
print()
print("----------------------------------- Вопросы к контрольной работе -----------------------------------")
print()
print(*[p.text for p in doc.paragraphs[138:153]], sep="\n")
print()
print("----------------------------------- Вопросы к зачёту -----------------------------------")
print()
print(*[p.text for p in doc.paragraphs[173:200]], sep="\n")
print()
print("----------------------------------- Вопросы для обсуждения на семинарских, практических занятиях -----------------------------------")
print()
for row in doc.tables[3].rows:
  print(row.cells[1].text)
  print()

----------------------------------- Наименование дисциплины -----------------------------------

Наименование дисциплины
«Прикладные задачи машинного обучения и обработки больших данных».

----------------------------------- Содержание дисциплины -----------------------------------

Содержание дисциплины
1. Реализация решений обработки больших данных.
Развертывание кластеров HDInsight. Прием данных для пакетной и интерактивной обработки: прием данных из облака или локальных данных. Управление Hadoop и Spark: создание и настройка кластера. Отладка заданий Hadoop и Spark. Прием данных в Apache Spark. Реализация пакетных решений для больших данных с помощью Spark. Реализация интерактивных запросов для больших данных с помощью Spark SQL. 
2. Информационные технологии анализа данных.
Задачи анализа данных, понятие набора данных (dataset). Подготовительные операции для выполнения анализа данных. Технологический стек анализа данных, построенный на базе языка программирования Python. Интеракти

##### Парсинг (тесты)

In [ ]:
# функция поиска индексов в списке строк по описанию раздела РПД
def search_index_by_string(string_list, keyword):
  matched_strings = list(filter(lambda x: keyword in x, string_list))

  if keyword == "вопросы для подготовки к зачету" and matched_strings == []:
    keyword = "вопросов для подготовки к зачету"
    matched_strings = list(filter(lambda x: keyword in x, string_list))
    if matched_strings == []:
      keyword = "вопросы для подготовки к экзамену"
      matched_strings = list(filter(lambda x: keyword in x, string_list))

  return [string_list.index(word) for word in matched_strings]

# доп функция парсинга, которая позволяет выявить в данных
# отдельные кейсы и фиксировать ключевые разделы документа
def dopparse(strok):
  if '5.1.' in strok or strok == 'содержание дисциплины' or strok == '5.1 содержание дисциплины':
    strok += ')))'
  elif '5.2' in strok or strok == 'учебно тематический план' or strok == '5.2 учебно тематический план' or strok == '. учебно тематический план' or strok == 'учебно – тематический план' or strok == '. учебно – тематический план':
    strok += ')))'
  elif '6.2' in strok or strok == 'перечень вопросов, заданий, тем для подготовки к текущему контролю' or strok == '6.2 перечень вопросов, заданий, тем для подготовки к текущему контролю' or strok == '. перечень вопросов, заданий, тем для подготовки к текущему контролю':
    strok += ')))'
  elif "«" in strok or '»' in strok:
    strok = strok.replace('«', '').replace('»', '')
  return strok

doc = docx.Document(docs_2023_path + files_2023[172])
text_paragraphs = [dopparse(' '.join(p.text.lower().strip().replace('\n', ' ').replace('\t', ' ').split('-'))) for p in doc.paragraphs if p.text != '']

###### Наименование дисциплины

In [ ]:
idx = search_index_by_string(text_paragraphs, "наименование дисциплины")[-1]
print(text_paragraphs[idx], text_paragraphs[idx+1], sep='\n')

1. наименование дисциплины
машинное зрение пми.


###### Содержание дисциплины

In [ ]:
main_start = search_index_by_string(text_paragraphs, "дисциплины)))")[-1]
main_end = search_index_by_string(text_paragraphs, "план)))")[-1]
print("Индексы начала и конца раздела содержания дисциплины:", main_start, main_end)
print()
print(*text_paragraphs[main_start+1:main_end], sep='\n')

Индексы начала и конца раздела содержания дисциплины: 28 41

тема1. введение в машинное зрение
история и основные понятия машинного зрения. задачи и проблемы машинного зрения. модели изображений в пространстве.
тема 2. классические методы машинного зрения
математический аппарат цифровой обработки изображений. выравнивание гистограмм. морфологические операции. обнаружение углов и границ.
тема 3. нейросетевые классификаторы изображений
линейные классификаторы изображений. svm классификатор. hinge loss. softmax классификатор. cross entropy loss. регуляризация классификатора изображений. оптимизация параметров (обучение) линейного классификатора изображений.
тема 4. сверточные нейронные сети
многослойные нелинейные классификаторы изображений. механизм обратного распространения ошибки. сверточные слои.
тема 5. сегментация и детекция
архитектуры современных нейросетей для извлечения признаков. кодирование и декодирование. семантическая сегментация. классификация с локализацией объекта. детек

In [ ]:
# idxs = search_index_by_string(text_paragraphs, "Содержание дисциплины")
# # idxs = search_index_by_string(text_paragraphs, "5.2.")
# print([p.text.strip() for p in doc.paragraphs])
# print([dopparse(' '.join(p.text.lower().strip().replace('\n', ' ').replace('\t', ' ').split('-'))) for p in doc.paragraphs])
# print()
# print(idxs)
# print(*[text_paragraphs[idx] for idx in idxs], sep='\n')

In [ ]:
# for ind in range(182):
#   doc = docx.Document(docs_2023_path + files_2023[ind])
#   print(f"{ind+1}) Документ 2023 года")
#   print(f"Название дока: {files_2023[ind]}")

#   text_paragraphs = [dopparse(' '.join(p.text.lower().strip().replace('\n', ' ').replace('\t', ' ').split('-'))) for p in doc.paragraphs]
#   # print(*text_paragraphs, sep='\n')

#   main_start = search_index_by_string(text_paragraphs, "дисциплины)))")
#   main_end = search_index_by_string(text_paragraphs, "план)))")
#   print()
#   print(main_start, main_end)
#   print()
#   # print(*text_paragraphs[main_start:main_end], sep='\n', end="\n")
#   print()

###### Вопросы к контрольной работе

In [ ]:
doc = docx.Document(docs_2020_path + files_2020[0])
text_paragraphs = [dopparse(' '.join(p.text.lower().strip().replace('\n', ' ').replace('\t', ' ').split('-'))) for p in doc.paragraphs if p.text != '']
idx = search_index_by_string(text_paragraphs, "текущему контролю)))")
if idx == []:
  # обработать кейс с отсутствием раздела 6.2. в РПД
  idx = ['0']
  idx = idx[-1]
  print(idx)
else:
  idx = idx[-1]
  print(idx)
  print(text_paragraphs[idx], *text_paragraphs[idx+1:idx+6], sep='\n')

78
перечень вопросов, заданий, тем для подготовки к текущему контролю)))
примерные вопросы к контрольной работе
1. задачи машинного обучения
2. метрические методы классификации
3. гипотеза компактности и непрерывности
4. метод ближайших соседей (knn) и его обобщения.


###### Вопросы к зачёту/экзамену

In [ ]:
for i in range(20):
  print(f'{i+1}) Документ {files_2021[i]}')
  doc = docx.Document(docs_2021_path + files_2021[i])
  text_paragraphs = [dopparse(' '.join(p.text.lower().strip().replace('\n', ' ').replace('\t', ' ').split('-'))) for p in doc.paragraphs if p.text != '']

  idx = search_index_by_string(text_paragraphs, "вопросы для подготовки к зачету")

  print(idx)
  idx = idx[-1]
  print(idx)
  print(text_paragraphs[idx], *text_paragraphs[idx+1:idx+100], sep='\n')

  print()
  print()
  print()

1) Документ Инт вещей, ПИ, 2021.docx
[115]
115
примерные вопросы для подготовки к зачету
история создания и развития интернета вещей.
архитектура интернета вещей.
типовые проекты интернета вещей.
технологические тренды в области интернета вещей.
безопасность интернета вещей.
примеры использования типовых регуляторов в системах автоматизации в интернете вещей.
примеры использования типовых фильтров при анализе данных в интернете вещей.
примеры использования методов идентификации и диагностики в интернете вещей.
примеры использования методов машинного обучения в интернете вещей.
структура платы arduino.
команды и библиотеки arduino.
интерфейсы и питание платы arduino.
синтаксис и структура кода в arduino.
цифровые входы/выходы. аналоговые сигналы платы arduino.
типы данных, переменные при программировании arduino
математические операции при программировании arduino
массивы при программировании arduino.
сравнения и условия. циклы. строки. функции при программировании arduino.
объекты и к

###### Вопросы к семинарским занятиям

In [ ]:
counter = 0
while True:
  if docs_2021_path + files_2021[counter] == '/content/gdrive/MyDrive/Диплом_Валяев/dataset/2021_year/Алгебра и геометрия, ПМИ.docx':
    print('YEEEEEEEEEEEEEEEEEEEEEEEESSSSSSSSSSSS')
    print(counter)
    break
  counter += 1

YEEEEEEEEEEEEEEEEEEEEEEEESSSSSSSSSSSS
48


In [ ]:
doc = docx.Document(docs_2020_path + files_2020[0])
tables = [[[cell.text.lower().strip() for cell in row.cells] for row in t.rows] for t in doc.tables]
seminars_ques = search_index_by_table(tables, 'перечень вопросов для обсуждения на семинар')
print(*seminars_ques, sep='\n\n')

1. использование кластера hdinsight
2. развертывание hadoop
3. настройка spark
4. построение моделей машинного обучения в spark
рекомендуемые источники:
основная литература – 8.[1],[2]
дополнительная литература - 9.[3], [5]

1. знакомство с информационными технологиями анализа данных
2. изучение технологического стека анализа данных, построенного на базе языка программирования python.
рекомендуемые источники:
основная литература – 8.[1],[2]
дополнительная литература - 9.[3], [4], [5]

1. изучение библиотеки scikit-learn для решения задач машинного обучения. 
2. обзор основных возможностей библиотеки решение базовых примеров и знакомство с основными этапами решения задач методами машинного обучения.
рекомендуемые источники:
основная литература – 8.[1],[2]
дополнительная литература - 9.[3], [4], [5]

1. формы визуализации результатов анализа данных. 
2. представление и интерпретация результатов, выявленных различными методами анализа данных.
рекомендуемые источники:
основная литература –

In [ ]:
for ind, file2021 in enumerate(files_2021):
  print(f'{ind+1}) Документ — {file2021}')
  doc = docx.Document(docs_2021_path + file2021)
  tables = [[[cell.text.lower().strip() for cell in row.cells] for row in t.rows] for t in doc.tables]
  seminars_ques = search_index_by_table(tables, 'наименование тем')
  print(seminars_ques)
  print(*seminars_ques, sep='\n')
  print()

1) Документ — Инт вещей, ПИ, 2021.docx
['Введение в «интернет вещей»', 'Архитектура и безопасность решений «интернета вещей»', 'Аппаратное обеспечение «интернета вещей»', 'Программное обеспечение «интернета вещей»', 'Реализация проектов «интернета вещей»']
Введение в «интернет вещей»
Архитектура и безопасность решений «интернета вещей»
Аппаратное обеспечение «интернета вещей»
Программное обеспечение «интернета вещей»
Реализация проектов «интернета вещей»

2) Документ — Агент мод.docx
['Основы агентно-ориентированного и имитационного моделирования', 'Моделирование случайных величин', 'Агентно-ориентированное моделирование', 'Обработка и интерпретация результатов агентно-ориентированного моделирования построение моделей']
Основы агентно-ориентированного и имитационного моделирования
Моделирование случайных величин
Агентно-ориентированное моделирование
Обработка и интерпретация результатов агентно-ориентированного моделирования построение моделей

3) Документ — Интел тех в УР.docx
['Поня

##### Парсинг

###### 2020 год

In [126]:
rpd_2020 = dict()
names_files_rpd_2020 = dict()
files_rpd_names_2020 = dict()

rpd_2020, names_files_rpd_2020, files_rpd_names_2020 = preprocessor.parsing_all_docs_year(docs_2020_path, files_2020, 2020)
dict(list(rpd_2020.items())[:5])

1) Документ РПД — Прикл задачи МОиОБД, Эк, КФУ.docx:
Название дисциплины — прикладные задачи машинного обучения и обработки больших данных

OK!


2) Документ РПД — Методы ВД,Эк,КФУ.docx:
Название дисциплины — методы визуализации данных

OK!


3) Документ РПД — Програм. на языках PYTHON и SQL,Эк, КФУ.docx:
Название дисциплины — программирование на языках python и sql

OK!


4) Документ РПД — Нейронные сети,Эк, КФУ.docx:
Название дисциплины — нейронные сети

OK!


5) Документ РПД — Обработка данных и мод. в МЕ,Эк, КФУ.docx:
Название дисциплины — обработка данных и моделирование в microsoft excel

OK!



ИТОГО количество повторений = 0
Словарь наименований РПД и файлов датасета 2020:
{'прикладные задачи машинного обучения и обработки больших данных 2020': 'Прикл задачи МОиОБД, Эк, КФУ.docx', 'методы визуализации данных 2020': 'Методы ВД,Эк,КФУ.docx', 'программирование на языках python и sql 2020': 'Програм. на языках PYTHON и SQL,Эк, КФУ.docx', 'нейронные сети 2020': 'Нейронные сети,Эк,

{'прикладные задачи машинного обучения и обработки больших данных 2020': (['1. реализация решений обработки больших данных.',
   'развертывание кластеров hdinsight. прием данных для пакетной и интерактивной обработки: прием данных из облака или локальных данных. управление hadoop и spark: создание и настройка кластера. отладка заданий hadoop и spark. прием данных в apache spark. реализация пакетных решений для больших данных с помощью spark. реализация интерактивных запросов для больших данных с помощью spark sql.',
   '2. информационные технологии анализа данных.',
   'задачи анализа данных, понятие набора данных (dataset). подготовительные операции для выполнения анализа данных. технологический стек анализа данных, построенный на базе языка программирования python. интерактивная оболочка ipython notebook: принципы работы и применение для решения задач анализа данных и машинного обучения. знакомство с библиотеками numpy и pandas.',
   '3. технологии машинного обучения.',
   'постановк

###### 2021 год

До решения проблемы переименования в итоговом словаре данных для будущего анализа было 64 ключа вместо 89 исходных!
Следовательно:
- «до» `counter_rep = 25`
- «после» `counter_rep = 0`

In [127]:
rpd_2021 = dict()
names_files_rpd_2021 = dict()
files_rpd_names_2021 = dict()

rpd_2021, names_files_rpd_2021, files_rpd_names_2021 = preprocessor.parsing_all_docs_year(docs_2021_path, files_2021, 2021)
dict(list(rpd_2021.items())[:5])

1) Документ РПД — Инт вещей, ПИ, 2021.docx:
Название дисциплины — интернет вещей

OK!


2) Документ РПД — Агент мод.docx:
Название дисциплины — агентное моделирование

OK!


3) Документ РПД — Интел тех в УР.docx:
Название дисциплины — интеллектуальные технологии в управлении рисками

OK!


4) Документ РПД — Соврем НТ, 2021.docx:
Название дисциплины — современные нейросетевые технологии

OK!


5) Документ РПД — Бухгалтерские ИС.docx:
Название дисциплины — бухгалтерские информационные системы

OK!


6) Документ РПД — Диф урав.docx:
Название дисциплины — дифференциальные уравнения

OK!


7) Документ РПД — Метод ПИДиПДДА.docx:
Название дисциплины — методология поиска источников данных и подготовки данных для анализа

OK!


8) Документ РПД — АС БУ АиА в КО.docx:
Название дисциплины — автоматизированные системы бухгалтерского учета, анализа и аудита в коммерческих организациях

OK!


9) Документ РПД — Прогр на яз Python и SQL, Эк.docx:
Название дисциплины — программирование на языках python

{'интернет вещей 2021': (['введение в интернет вещей',
   'понятие интернет вещей. примеры и основные области применения интернета вещей. отраслевые вертикали, которые используют технологии интернета вещей. отличительные особенности устройств интернета вещей коммерческого применения от потребительского применения. история появления и развития интернета вещей.',
   'архитектура и безопасность решений интернета вещей',
   'уровни архитектуры интернета вещей. компоненты архитектуры интернета вещей. источники данных интернета вещей. машинное обучение в интернете вещей. способы передачи данных в интернете вещей. безопасность интернета вещей. технологические тренды в области интернета вещей.',
   'аппаратное обеспечение интернета вещей',
   'роль аппаратного обеспечения в архитектуре интернета вещей. виды аппаратного обеспечения интернета вещей. программируемые логические контроллеры (плк), датчики, исполнительные устройства. подключение датчиков к плк и микроконтроллерам. ознакомление с вид

In [130]:
len(list(rpd_2021.keys())), len(files_2021)

(89, 89)

###### 2022 год

До решения проблемы переименования в итоговом словаре данных для будущего анализа было 92 ключа вместо 129 исходных!
Следовательно:
- «до» `counter_rep = 25 + 37 = 62`
- «после» `counter_rep = 0`

In [128]:
rpd_2022 = dict()
names_files_rpd_2022 = dict()
files_rpd_names_2022 = dict()

rpd_2022, names_files_rpd_2022, files_rpd_names_2022 = preprocessor.parsing_all_docs_year(docs_2022_path, files_2022, 2022)
dict(list(rpd_2022.items())[:5])

1) Документ РПД — MLOps, 2022.docx:
Название дисциплины — mlops

OK!


2) Документ РПД — Современные ТП, з, 2021.docx:
Название дисциплины — современные технологии программирования

OK!


3) Документ РПД — Диф уравнения, 2022.docx:
Название дисциплины — дифференциальные уравнения

OK!


4) Документ РПД — Хранилища данных, 2022.docx:
Название дисциплины — хранилища данных

OK!


5) Документ РПД — Прикладные задачи МО, Эк, 2022.docx:
Название дисциплины — дисциплина прикладные задачи машинного обучения

OK!


6) Документ РПД — Вирт и конт. 2022.docx:
Название дисциплины — виртуализация и контейнеризация

OK!


7) Документ РПД — Прикл мод и МТСС, 2022.docx:
Название дисциплины — прикладные модели и методы теории сложных сетей

OK!


8) Документ РПД — ОД на языке SQL (MS SQL), 2022.docx:
Название дисциплины — обработка данных на языке sql (ms sql)

OK!


9) Документ РПД — Методы работы с БИ, 2022.DOCX:
Название дисциплины — методы работы с базами изображений

OK!


10) Документ РПД — Алгор

{'mlops 2022': (['тема 1. введение в mlops',
   'что такое mlops и зачем он нужен. определение интеллектуальных информационных систем. особенности иис. жизненный цикл программного обеспечения. неприменимость классических моделей жизненного цикла к иис.',
   'методология mlops. принципы devops и data science в mlops. контроль версий и автоматизированные сборочные процессы.',
   'тема 2. инфраструктура для автоматизации процесса разработки, обучения и развертывания моделей машинного обучения',
   'как создать инфраструктуру для mlops. настройка среды разработки и обучения моделей. настройка инструментов для автоматического развертывания моделей. встраивание моделей машинного обучения в информационные продукты. инфраструктура иис. зависимость от внешней среды.',
   'взаимосвязь разработки в ноутбуках и продуктовом окружении.',
   'тема 3. непрерывная интеграция и доставка в mlops',
   'классический конвейер ci/cd. особенности иис. основные риски. этапизация проекта по разработке и внедрен

In [131]:
len(list(rpd_2022.keys())), len(files_2022)

(129, 129)

###### 2023 год

До решения проблемы переименования в итоговом словаре данных для будущего анализа было 128 ключа вместо 183 исходных!
Следовательно:
- «до» `counter_rep = 55 + 37 + 25 = 117`
- «после» `counter_rep = 0`

In [129]:
rpd_2023 = dict()
names_files_rpd_2023 = dict()
files_rpd_names_2023 = dict()

rpd_2023, names_files_rpd_2023, files_rpd_names_2023 = preprocessor.parsing_all_docs_year(docs_2023_path, files_2023, 2023)
dict(list(rpd_2023.items())[:5])

1) Документ РПД — МО на графах, МО на ТиГ, 2023.docx:
Название дисциплины — машинное обучение на графах

OK!


2) Документ РПД — Интерактивные ТСКП, 2022.docx:
Название дисциплины — интерактивные технологии современных коммуникационных платформ

OK!


3) Документ РПД — Технологии ОиАБД, Эк, 2022.docx:
Название дисциплины — технологии обработки и анализа больших данных

OK!


4) Документ РПД — Основы СА, ПИ, DO-И, 2023.docx:
Название дисциплины — основы сетевого администрирования

OK!


5) Документ РПД — Управление КПС, 2021.docx:
Название дисциплины — управление качеством программных систем

OK!


6) Документ РПД — Инстр Power BI и Excel в лог, 2022.docx:
Название дисциплины — инструменты power bi и excel в логистике

OK!


7) Документ РПД — Программ на яз Python  и SQL, 2022.docx:
Название дисциплины — программирование на языках python и sql

OK!


8) Документ РПД — Визуализация данных, 2021, 2022.docx:
Название дисциплины — визуализация данных

OK!


9) Документ РПД — Математика МТС,

{'машинное обучение на графах 2023': (['тема 1. введение в искусственные нейронные сети и глубокое обучение.',
   'персептрон. схема работы, функция активации и ее варианты, проблема по',
   'знакомство с базовыми понятиями инс.',
   'принципы построения моделей глубокого обучения. методы обучения нейронной сети и обратное распространение ошибки. обучение модели нейронной сети, алгоритм обратного распространения ошибки. проблема обучения модели нейронной сети. проблема поиска градиента. дифференцируемое программирование и реализация обратного распространения ошибки.',
   'основы построения моделей инс в pytorch. загрузка и преобразование данных в pytorch. тензоры и опреации с ними в pytorch: создание тензоров, операции с тензорами. арифметические операции и математические функции: операции, изменяющие размер тензора, операции агрегации, матричные операции. автоматическое дифференцирование в pytorch. знакомство с основным циклом обучения в pytorch на примере решения задачи регрессии.',


In [132]:
len(list(rpd_2023.keys())), len(files_2023)

(183, 183)

#### 2 стадия предобработки

##### Слияние данных всех лет

In [133]:
(len(rpd_2020) + len(rpd_2021) + len(rpd_2022) + len(rpd_2023),
 len(names_files_rpd_2020) + len(names_files_rpd_2021) + len(names_files_rpd_2022) + len(names_files_rpd_2023),
 len(files_rpd_names_2020) + len(files_rpd_names_2021) + len(files_rpd_names_2022) + len(files_rpd_names_2023))

(406, 406, 406)

In [134]:
rpd_all_data = dict()
rpd_all_data.update(rpd_2020)

name_to_file_rpd = dict()
name_to_file_rpd.update(names_files_rpd_2020)

file_to_name_rpd = dict()
file_to_name_rpd.update(files_rpd_names_2020)
file_to_name_rpd

{'Прикл задачи МОиОБД, Эк, КФУ.docx': {'NAME': 'Прикладные задачи машинного обучения и обработки больших данных',
  'THEMES': ['Реализация решений обработки больших данных',
   'Информационные технологии анализа данных',
   'Технологии машинного обучения',
   'Визуализация результатов анализа данных'],
  'LINKDOC': 'vk.cc/cvqvsb'},
 'Методы ВД,Эк,КФУ.docx': {'NAME': 'Методы визуализации данных',
  'THEMES': ['Принципы визуализации',
   'Пакет ms office excel область применимости, текстовые и логические функции',
   'Пакет microsoft power bi область применимости, основные функции',
   'Визуализация результатов анализа данных на языке python'],
  'LINKDOC': 'vk.cc/cvqvs8'},
 'Програм. на языках PYTHON и SQL,Эк, КФУ.docx': {'NAME': 'Программирование на языках python и sql',
  'THEMES': ['Использование языков python и sql, типы данных',
   'Программирование на языке python',
   'Программирование на языке sql'],
  'LINKDOC': 'vk.cc/cvqvs4'},
 'Нейронные сети,Эк, КФУ.docx': {'NAME': 'Нейрон

In [135]:
# проверка работы слияния словарей данных
assert rpd_all_data == rpd_2020
assert name_to_file_rpd == names_files_rpd_2020
assert file_to_name_rpd == files_rpd_names_2020

In [136]:
# добавление оставшихся словарей данных
rpd_all_data.update(rpd_2021)
rpd_all_data.update(rpd_2022)
rpd_all_data.update(rpd_2023)

name_to_file_rpd.update(names_files_rpd_2021)
name_to_file_rpd.update(names_files_rpd_2022)
name_to_file_rpd.update(names_files_rpd_2023)

file_to_name_rpd.update(files_rpd_names_2021)
file_to_name_rpd.update(files_rpd_names_2022)
file_to_name_rpd.update(files_rpd_names_2023)

(len(rpd_all_data.keys()), len(name_to_file_rpd.keys()), len(file_to_name_rpd.keys()))

(406, 406, 406)

In [137]:
dict(list(name_to_file_rpd.items())[:10])

{'прикладные задачи машинного обучения и обработки больших данных 2020': 'Прикл задачи МОиОБД, Эк, КФУ.docx',
 'методы визуализации данных 2020': 'Методы ВД,Эк,КФУ.docx',
 'программирование на языках python и sql 2020': 'Програм. на языках PYTHON и SQL,Эк, КФУ.docx',
 'нейронные сети 2020': 'Нейронные сети,Эк, КФУ.docx',
 'обработка данных и моделирование в microsoft excel 2020': 'Обработка данных и мод. в МЕ,Эк, КФУ.docx',
 'интернет вещей 2021': 'Инт вещей, ПИ, 2021.docx',
 'агентное моделирование 2021': 'Агент мод.docx',
 'интеллектуальные технологии в управлении рисками 2021': 'Интел тех в УР.docx',
 'современные нейросетевые технологии 2021': 'Соврем НТ, 2021.docx',
 'бухгалтерские информационные системы 2021': 'Бухгалтерские ИС.docx'}

In [138]:
list(rpd_all_data.keys())[:20]

['прикладные задачи машинного обучения и обработки больших данных 2020',
 'методы визуализации данных 2020',
 'программирование на языках python и sql 2020',
 'нейронные сети 2020',
 'обработка данных и моделирование в microsoft excel 2020',
 'интернет вещей 2021',
 'агентное моделирование 2021',
 'интеллектуальные технологии в управлении рисками 2021',
 'современные нейросетевые технологии 2021',
 'бухгалтерские информационные системы 2021',
 'дифференциальные уравнения 2021',
 'методология поиска источников данных и подготовки данных для анализа 2021',
 'автоматизированные системы бухгалтерского учета, анализа и аудита в коммерческих организациях 2021',
 'программирование на языках python и sql 2021',
 'современные технологии программирования 2021',
 'программирование и анализ данных с помощью python 2021',
 'рекомендательные системы 2021',
 'прикладные задачи машинного обучения и обработки больших данных 2021',
 'прикладные модели и методы теории сложных сетей 2021',
 'агентно ориен

In [139]:
dict(list(file_to_name_rpd.items())[:5])

{'Прикл задачи МОиОБД, Эк, КФУ.docx': {'NAME': 'Прикладные задачи машинного обучения и обработки больших данных',
  'THEMES': ['Реализация решений обработки больших данных',
   'Информационные технологии анализа данных',
   'Технологии машинного обучения',
   'Визуализация результатов анализа данных'],
  'LINKDOC': 'vk.cc/cvqvsb'},
 'Методы ВД,Эк,КФУ.docx': {'NAME': 'Методы визуализации данных',
  'THEMES': ['Принципы визуализации',
   'Пакет ms office excel область применимости, текстовые и логические функции',
   'Пакет microsoft power bi область применимости, основные функции',
   'Визуализация результатов анализа данных на языке python'],
  'LINKDOC': 'vk.cc/cvqvs8'},
 'Програм. на языках PYTHON и SQL,Эк, КФУ.docx': {'NAME': 'Программирование на языках python и sql',
  'THEMES': ['Использование языков python и sql, типы данных',
   'Программирование на языке python',
   'Программирование на языке sql'],
  'LINKDOC': 'vk.cc/cvqvs4'},
 'Нейронные сети,Эк, КФУ.docx': {'NAME': 'Нейрон

##### Очистка от пунктуации

In [140]:
rpd_data = preprocessor.clearing_data_punkt(rpd_all_data)

1) прикладные задачи машинного обучения и обработки больших данных 2020
OK!


2) методы визуализации данных 2020
OK!


3) программирование на языках python и sql 2020
OK!


4) нейронные сети 2020
OK!


5) обработка данных и моделирование в microsoft excel 2020
OK!


6) интернет вещей 2021
OK!


7) агентное моделирование 2021
OK!


8) интеллектуальные технологии в управлении рисками 2021
OK!


9) современные нейросетевые технологии 2021
OK!


10) бухгалтерские информационные системы 2021
OK!


11) дифференциальные уравнения 2021
OK!


12) методология поиска источников данных и подготовки данных для анализа 2021
OK!


13) автоматизированные системы бухгалтерского учета, анализа и аудита в коммерческих организациях 2021
OK!


14) программирование на языках python и sql 2021
OK!


15) современные технологии программирования 2021
OK!


16) программирование и анализ данных с помощью python 2021
OK!


17) рекомендательные системы 2021
OK!


18) прикладные задачи машинного обучения и обработки

In [141]:
dict(list(rpd_data.items())[:5])

{'прикладные задачи машинного обучения и обработки больших данных 2020': {'SODERZ': ['реализация решений обработки больших данных',
   'развертывание кластеров hdinsight прием данных для пакетной и интерактивной обработки прием данных из облака или локальных данных управление hadoop и spark создание и настройка кластера отладка заданий hadoop и spark прием данных в apache spark реализация пакетных решений для больших данных с помощью spark реализация интерактивных запросов для больших данных с помощью spark sql',
   'информационные технологии анализа данных',
   'задачи анализа данных понятие набора данных dataset подготовительные операции для выполнения анализа данных технологический стек анализа данных построенный на базе языка программирования python интерактивная оболочка ipython notebook принципы работы и применение для решения задач анализа данных и машинного обучения знакомство с библиотеками numpy и pandas',
   'технологии машинного обучения',
   'постановки задач машинного обу

### Предобработка данных для ботов

##### Клавиатурная структура кнопок

Общий вид структуры клавиатуры РПДшек по годам:
- год
  - направления подготовки
    - общие сферы деятельности
      - дисциплины

###### 2020 год

Тут всё проще, поскольку, исходя из датасета, мы имеем 5 файлов РПД, которые спокойно размещаются на клавиатуре по кнопкам:

- Методы ВД,Эк,КФУ.docx
- Нейронные сети,Эк, КФУ.docx
- Обработка данных и мод. в МЕ,Эк, КФУ.docx
- Прикл задачи МОиОБД, Эк, КФУ.docx
- Програм. на языках PYTHON и SQL,Эк, КФУ.docx

###### 2021 год

In [142]:
tituls_2021 = []
tituls_2021 = preprocessor.get_tituls_rpd(docs_2021_path, files_2021, 2021)

Титульные страницы РПД 2021 года:


1) Документ — Инт вещей, ПИ, 2021.docx

департамент анализа данных и машинного обучения
факультета информационных технологий и анализа больших данных
базанов к.г.
интернет вещей
рабочая программа дисциплины
для студентов, обучающихся по направлению подготовки
09.04.03 прикладная информатика,
направленность программы магистратуры:
обработка больших данных и разработка интеллектуальных приложений

['09.04.03', 'прикладная информатика']


2) Документ — Агент мод.docx

д. и. коровин
агентное моделирование
рабочая программа дисциплины
для обучающихся по направлению подготовки
09.06.01 информатика и вычислительная техника,
направленность программы   математическое моделирование,
численные методы и комплексы программ
(подготовка научно педагогических кадров в аспирантуре)

['09.06.01', 'информатика и вычислительная техника']


3) Документ — Интел тех в УР.docx

департамент анализа данных и машинного обучения
факультета информационных технологий и анализа б

In [143]:
tituls_2021[:10]

[{'Инт вещей, ПИ, 2021.docx': ['09.04.03', 'прикладная информатика']},
 {'Агент мод.docx': ['09.06.01', 'информатика и вычислительная техника']},
 {'Интел тех в УР.docx': ['01.04.02', 'прикладная математика и информатика']},
 {'Соврем НТ, 2021.docx': ['01.04.02', 'прикладная математика и информатика']},
 {'Бухгалтерские ИС.docx': ['01.03.02',
   'прикладная математика и информатика']},
 {'Диф урав.docx': ['01.03.02', 'прикладная математика и информатика']},
 {'Метод ПИДиПДДА.docx': ['01.04.02', 'прикладная математика и информатика']},
 {'АС БУ АиА в КО.docx': ['09.04.03', 'прикладная информатика']},
 {'Прогр на яз Python и SQL, Эк.docx': ['38.04.01', 'экономика']},
 {'СоврТП, ПИ.docx': ['09.03.03', 'прикладная информатика']}]

In [144]:
count_napravs_2021 = preprocessor.agg_count_napravs_year(tituls_2021)
count_napravs_2021

{'лингвистика': [4,
  ['Интер тех СКП ПУ.docx',
   'Интер тех СКП.docx',
   'Основы МОЕЯ (NLP).DOCX',
   'Тех обеспеч ИАиДК.docx']],
 'бизнес информатика': [4,
  ['Алгоритмы и СД в яз Python, БИ.docx',
   'Базы данных, БИ.docx',
   'Математика, БИ.docx',
   'ТВиМС, БИ.docx']],
 'экономика': [12,
  ['Аналит ИТиС, Эк.docx',
   'Большие данные и МО, Эк.docx',
   'Инстр-ые средства СФ, Эк, ФТБ.docx',
   'Интеллект ИС (Эк, 2021).docx',
   'МиИМЭ, Эк, 2021.docx',
   'Прикл задачи МОиОБД, Эк.docx',
   'Прогр на яз Python и SQL, Эк.docx',
   'Сложные СиГ (Эк, 2021).docx',
   'Соврем ТИАТиДС, Эк, 2021.docx',
   'Современные ТКЗ, Эк.docx',
   'Финтех (ФРО).docx',
   'Финтех (Эк).docx']],
 'прикладная информатика': [28,
  ['А-О мод, (ПИ, з, 2021).docx',
   'АС БУ АиА в КО.docx',
   'Автоматизированные БСиДБС, ПИ.docx',
   'Алгебра и анализ, ПИ.docx',
   'Алгоритмы и СД в яз Python, ПИ.docx',
   'Алгоритмы и ТАСС.docx',
   'Анализ ПС.docx',
   'Блокчейн-платформы.docx',
   'Введение в спец., ПИ.d

In [145]:
not_others = ['Большие данные и МО, Эк.docx', 'Прикл задачи МОиОБД, Эк.docx', 'Прогр на яз Python и SQL, Эк.docx', 'Соврем ТИАТиДС, Эк, 2021.docx', 'Современные ТКЗ, Эк.docx']

[elem for elem in count_napravs_2021['экономика'][1] if elem not in not_others]

['Аналит ИТиС, Эк.docx',
 'Инстр-ые средства СФ, Эк, ФТБ.docx',
 'Интеллект ИС (Эк, 2021).docx',
 'МиИМЭ, Эк, 2021.docx',
 'Сложные СиГ (Эк, 2021).docx',
 'Финтех (ФРО).docx',
 'Финтех (Эк).docx']

In [146]:
[(elem, elem in count_napravs_2021['экономика'][1]) for elem in not_others]

[('Большие данные и МО, Эк.docx', True),
 ('Прикл задачи МОиОБД, Эк.docx', True),
 ('Прогр на яз Python и SQL, Эк.docx', True),
 ('Соврем ТИАТиДС, Эк, 2021.docx', True),
 ('Современные ТКЗ, Эк.docx', True)]

Клавиатура для 2021 года:
- БИ (4)
- ИБ (6)
- ИВТ (5)
- Инноватика (2)
- Лингвистика (4)
- Менеджмент (1)
- МехиРоб (2)
- ПИ (28)
  - Аналитика (7)
    - Алгоритмы и ТАСС.docx
    - Интеллект ИС.docx
    - Нереляционные БД, ПИ.DOCX
    - ПМиМАНИ, ПИ.docx
    - СУБД (ПИ).docx
    - Совр комп тех МО, ПИ.docx
    - Технол обр БД, ПИ.docx
  - Математика (4)
    - Алгебра и анализ, ПИ.docx
    - Дискрет матем, ПИ.docx
    - ТВиМС, ПИ.docx
    - Фин мат и ее прил, ПИ.docx
  - Разработка (5)
    - Алгоритмы и СД в яз Python, ПИ.docx
    - Организация ВС.docx
    - Практик по пр-нию, ПИ.docx
    - Сетевые СиП.docx
    - СоврТП, ПИ.docx
  - Системы (5)
    - А-О мод, (ПИ, з, 2021).docx
    - Геоинформ. системы.docx
    - Информ СЭА.docx
    - Комп мод ЭиФС.docx
    - Проектирование ИС.docx
  - Прочие (7)
- ПМИ (24)
  - Аналитика (10)
    - Алгоритмы и СД в яз Python, ПМИ.docx
    - Введение в НоД, ПМИ.docx
    - Интел тех в УР.docx
    - Метод ПИДиПДДА.docx
    - Методы ВД,.docx
    - ПМиМАНИ, ПМИ.docx
    - Реком системы.docx
    - СУБД (ПМИ).docx
    - Соврем НТ, 2021.docx
    - Технологии ОБД.docx
  - Математика (6)
    - Алгебра и геометрия, ПМИ.docx
    - Дискрет матем, ПМИ.docx
    - Диф урав.docx
    - Мат. анализ, ПМИ.docx
    - ТВиМС, ПМИ.docx
    - Фин мат и ее прил, ПМИ.docx
  - Прочие (8)
- Туризм (1)
- Экономика (12)
  - Аналитика (5)
    - Большие данные и МО, Эк.docx
    - Прикл задачи МОиОБД, Эк.docx
    - Прогр на яз Python и SQL, Эк.docx
    - Соврем ТИАТиДС, Эк, 2021.docx
    - Современные ТКЗ, Эк.docx
  - Прочие (7)

###### 2022 год

In [147]:
tituls_2022 = []
tituls_2022 = preprocessor.get_tituls_rpd(docs_2022_path, files_2022, 2022)

Титульные страницы РПД 2022 года:


1) Документ — MLOps, 2022.docx

департамент анализа данных и машинного обучения
факультета информационных технологий и анализа больших данных
утверждаю
проректор по учебной                и методической работе
__________ е.а. каменева
22.12.2022 г.
м.в. коротеев
mlops
рабочая программа дисциплины
для студентов, обучающихся по направлению подготовки
09.04.03   прикладная информатика,
направленность программы:
«программное управление операциями разработки информационных систем»
рекомендовано ученым советом
факультета информационных технологий и анализа больших данных
(протокол №27 от 15.12.2022г.)

['09.04.03', 'прикладная информатика']


2) Документ — Современные ТП, з, 2021.docx

д. м. милованов
современные технологии программирования
рабочая программа дисциплины
для студентов, обучающихся
по направлению подготовки 09.03.03   прикладная информатика,
оп «прикладная информатика»,
профиль «высокопроизводительные вычисления в цифровой экономике»
рекоменд

In [148]:
tituls_2022[:10]

[{'MLOps, 2022.docx': ['09.04.03', 'прикладная информатика']},
 {'Современные ТП, з, 2021.docx': ['09.03.03', 'прикладная информатика']},
 {'Диф уравнения, 2022.docx': ['01.03.02',
   'прикладная математика и информатика']},
 {'Хранилища данных, 2022.docx': ['09.03.03', 'прикладная информатика']},
 {'Прикладные задачи МО, Эк, 2022.docx': ['38.04.01', 'экономика']},
 {'Вирт и конт. 2022.docx': ['09.04.03', 'прикладная информатика']},
 {'Прикл мод и МТСС, 2022.docx': ['01.04.02',
   'прикладная математика и информатика']},
 {'ОД на языке SQL (MS SQL), 2022.docx': ['09.04.03',
   'прикладная информатика']},
 {'Методы работы с БИ, 2022.DOCX': ['01.04.02',
   'прикладная математика и информатика']},
 {'Алгоритмы ТГ, 2022.docx': ['01.04.02',
   'прикладная математика и информатика']}]

In [149]:
count_napravs_2022 = preprocessor.agg_count_napravs_year(tituls_2022)
count_napravs_2022

{'лингвистика': [1, ['Основы МОЕЯ (NLP), 2022.DOCX']],
 'бизнес информатика': [4,
  ['Алг и СД в яз Python (БИ, 2022).docx',
   'Мат методы ПР, БИ, 2022.docx',
   'Математика (БИ, 2022).docx',
   'ТВиМС, БИ, 2022.docx']],
 'экономика': [12,
  ['АСБУАиАвКО, Эк,2022.docx',
   'Большие данные и МО вСС, 2021, 2022.docx',
   'Интеллект ИС, Эк, 2022.docx',
   'Интеллект тех в УР,  2022.docx',
   'МСиИМвЭ, Эк, 2022.docx',
   'Методы ВД, Эк, 2022.docx',
   'Нейрон сети.docx',
   'ОД и мод в МЕ, Эк, 2022.docx',
   'Прикладные задачи МО, Эк, 2022.docx',
   'Программ на  яз Python и  SQL, 2022.docx',
   'Современные ТГО, Эк.docx',
   'Финтех, Эк, 2022.docx']],
 'прикладная информатика': [52,
  ['MLOps, 2022.docx',
   'NoSQL СУБД, 2022.docx',
   'Алг и СД в яз Python (ПИ, 2022).docx',
   'Алг и анализ (2022).docx',
   'Банковские ИС, ПИ, 2021, 2022.docx',
   'Введ в НоД (ПИ, 2022).docx',
   'Введ в спец, ПИ, 2022.docx',
   'Веб-разработка, 2021.docx',
   'Вирт и конт. 2022.docx',
   'Виртуализаци

In [150]:
not_others = ['Алг и СД в яз Python, ПМИ, 2022.docx', 'Введ в НоД, (ПМИ, 2022).docx', 'Метод ПИДиПДдА,ПМИ, 2022.docx', 'Методы ВД (ПМИ, 2022).docx', 'ОД и моделир в МЕ, ПМИ, 2022.docx', 'Тех разработки ЧБ, 2022.docx', 'ТОД, ПМИ, 2022.docx', 'Функц анализ, ПМИ,  2021, 2022.docx', 'Эконометрика, ПМИ, 2021, 2022.docx', 'Графовые БД, 2022.docx', 'КО и сист РИ, ПМИ, 2022.docx', 'Нереляц БД (ПМИ, 2022).docx', 'Обр текстов на ЕЯ, ПМИ, 2022.docx', 'Пред аналитика БД, ПМИ, 2022.docx', 'Представление и ОМИ, 2022.docx', 'Современные ТОТ на ест яз, 2022.docx', 'СУБД, ПМИ, 2022.docx', 'Алгебра и геом (2022).docx', 'Алгоритмы ТГ, 2022.docx', 'Дискрет матем (ПМИ, 2022).docx', 'Диф уравнения, 2022.docx', 'Мат методы ПР,ПМИ,2022.docx', 'Мат. анализ (2022).docx', 'Методы оптимизции,2021,2022.DOCX', 'Прикл мод и МТСС, 2022.docx', 'ТВиМС, ПМИ, 2022.docx', 'Фин мат и ее прил, ПМИ, 2022.docx', 'Глубокое обучение, ПМИ, 2022.docx', 'МО на графах, 2022.docx', 'Машинное обуч,ПМИ,2022.docx', 'Машинное обучение, 2021.docx', 'Методы работы с БИ, 2022.DOCX', 'Модели и МГИ, 2022.docx', 'Обуч с подкр, 2022.docx', 'Оптим систем КЗ, 2022.docx', 'Построение и ОММО, 2022.docx', 'Современные НТ, 2022.docx']

[elem for elem in count_napravs_2022['прикладная математика и информатика'][1] if elem not in not_others]

['Введ в спец, (ПМИ,  2022).docx',
 'Практик по прогр (ПМИ, 2022).docx',
 'Прикл мод и МКЗ, 2022.DOCX',
 'Проектирование АИС, ПМИ, 2022, 2023.docx',
 'ФУ_ИиС (ПМИ, 2022).docx',
 'Цифровая ОИ, 2022.docx',
 'Числ методы, ПМИ 2021,2022.docx']

In [151]:
[(elem, elem in count_napravs_2022['прикладная математика и информатика'][1]) for elem in not_others]

[('Алг и СД в яз Python, ПМИ, 2022.docx', True),
 ('Введ в НоД, (ПМИ, 2022).docx', True),
 ('Метод ПИДиПДдА,ПМИ, 2022.docx', True),
 ('Методы ВД (ПМИ, 2022).docx', True),
 ('ОД и моделир в МЕ, ПМИ, 2022.docx', True),
 ('Тех разработки ЧБ, 2022.docx', True),
 ('ТОД, ПМИ, 2022.docx', True),
 ('Функц анализ, ПМИ,  2021, 2022.docx', True),
 ('Эконометрика, ПМИ, 2021, 2022.docx', True),
 ('Графовые БД, 2022.docx', True),
 ('КО и сист РИ, ПМИ, 2022.docx', True),
 ('Нереляц БД (ПМИ, 2022).docx', True),
 ('Обр текстов на ЕЯ, ПМИ, 2022.docx', True),
 ('Пред аналитика БД, ПМИ, 2022.docx', True),
 ('Представление и ОМИ, 2022.docx', True),
 ('Современные ТОТ на ест яз, 2022.docx', True),
 ('СУБД, ПМИ, 2022.docx', True),
 ('Алгебра и геом (2022).docx', True),
 ('Алгоритмы ТГ, 2022.docx', True),
 ('Дискрет матем (ПМИ, 2022).docx', True),
 ('Диф уравнения, 2022.docx', True),
 ('Мат методы ПР,ПМИ,2022.docx', True),
 ('Мат. анализ (2022).docx', True),
 ('Методы оптимизции,2021,2022.DOCX', True),
 ('При

Клавиатура для 2022 года:
- БИ (4)
- ИБ (6)
- ИВТ (2)
- Инноватика (3)
- Лингвистика (1)
- Менеджмент (1)
- МехиРоб (4)
- ПИ (52)
  - Аналитика (7)
    - NoSQL СУБД, 2022.docx
    - Введ в НоД (ПИ, 2022).docx
    - Методы ВД, ПИ, 2022.docx
    - ОД и моделир в МЕ, ПИ, 2022.docx
    - ОД на языке DAX,  2022.docx
    - ОД на языке SQL (MS SQL), 2022.docx
    - ТОД, ПИ,  2022.docx
  - Большие данные (9)
    - Нереляц БД, (ПИ, 2022).docx
    - Обработка СПБД, з, 2021, 2022.docx
    - Обработка СиПБД, о, 2022.docx
    - Пред аналитика БД, ПИ, 2022.docx
    - Пред аналитика БД, м, ПИ, 2022.docx
    - СУБД,ПИ,2022.docx
    - ТОБД, (ПИ, з, 2022).docx
    - Тех обработки БД,  2022.docx
    - Хранилища данных, 2022.docx
  - Математика (4)
    - Алг и анализ (2022).docx
    - Дискрет матем (ПИ, 2022).docx
    - ТВиМС, ПИ, 2022.docx
    - Фин мат и ее прил, ПИ, 2022.docx
  - Машинное обучение (6)
    - MLOps, 2022.docx
    - Глубокое обучение, ПИ, 2022.docx
    - Маш зрение, 2021.docx
    - Маш обучение, ПИ, 2022.docx
    - Машинное обуч,ПИ,2022.docx
    - Обр текстов на ЕЯ, ПИ, 2022.docx
  - Разработка (10)
    - Алг и СД в яз Python (ПИ, 2022).docx
    - Веб-разработка, 2021.docx
    - Вирт и конт. 2022.docx
    - Виртуализация, 2022.docx
    - Инфраструктура как код, 2022.docx
    - Облачные тех-ии, ПИ, 2022.docx
    - Организация ВС (2022).docx
    - Практик по прогр (ПИ, 2022).docx
    - Прогр инженерия, 2021, 2022.docx
    - Современные ТП, з, 2021.docx
  - Системы (7)
    - Банковские ИС, ПИ, 2021, 2022.docx
    - Имитационное и АМ, 2021.docx
    - Интеллект ИС,ПИ,2022.docx
    - Комп мод ЭиФС, 2022.docx
    - Основы СА,  2022.docx
    - Прикладные ИС, ПИ, 2021.docx
    - Проектирование АИС, ПИ, 2022, 2023.docx
  - Прочие (9)
- ПМИ (44)
  - Аналитика (9)
    - Алг и СД в яз Python, ПМИ, 2022.docx
    - Введ в НоД, (ПМИ, 2022).docx
    - Метод ПИДиПДдА,ПМИ, 2022.docx
    - Методы ВД (ПМИ, 2022).docx
    - ОД и моделир в МЕ, ПМИ, 2022.docx
    - Тех разработки ЧБ, 2022.docx
    - ТОД, ПМИ, 2022.docx
    - Функц анализ, ПМИ,  2021, 2022.docx
    - Эконометрика, ПМИ, 2021, 2022.docx
  - Большие данные (8)
    - Графовые БД, 2022.docx
    - КО и сист РИ, ПМИ, 2022.docx
    - Нереляц БД (ПМИ, 2022).docx
    - Обр текстов на ЕЯ, ПМИ, 2022.docx
    - Пред аналитика БД, ПМИ, 2022.docx
    - Представление и ОМИ, 2022.docx
    - Современные ТОТ на ест яз, 2022.docx
    - СУБД, ПМИ, 2022.docx
  - Математика (10)
    - Алгебра и геом (2022).docx
    - Алгоритмы ТГ, 2022.docx
    - Дискрет матем (ПМИ, 2022).docx
    - Диф уравнения, 2022.docx
    - Мат методы ПР,ПМИ,2022.docx
    - Мат. анализ (2022).docx
    - Методы оптимизции,2021,2022.docx
    - Прикл мод и МТСС, 2022.docx
    - ТВиМС, ПМИ, 2022.docx
    - Фин мат и ее прил, ПМИ, 2022.docx
  - Машинное обучение (10)
    - Глубокое обучение, ПМИ, 2022.docx
    - МО на графах, 2022.docx
    - Машинное обуч,ПМИ,2022.docx
    - Машинное обучение, 2021.docx
    - Методы работы с БИ, 2022.docx
    - Модели и МГИ, 2022.docx
    - Обуч с подкр, 2022.docx
    - Оптим систем КЗ, 2022.docx
    - Построение и ОММО, 2022.docx
    - Современные НТ, 2022.docx
  - Прочие (7)
- Экономика (12)
  - Аналитика (7)
    - Большие данные и МО вСС, 2021, 2022.docx
    - Методы ВД, Эк, 2022.docx
    - Нейрон сети.docx
    - ОД и мод в МЕ, Эк, 2022.docx
    - Прикладные задачи МО, Эк, 2022.docx
    - Программ на  яз Python и  SQL, 2022.docx
    - Современные ТГО, Эк.docx
  - Прочие (5)

###### 2023 год

In [152]:
tituls_2023 = []
tituls_2023 = preprocessor.get_tituls_rpd(docs_2023_path, files_2023, 2023)

Титульные страницы РПД 2023 года:


1) Документ — МО на графах, МО на ТиГ, 2023.docx

факультета информационных технологий и анализа больших данных
с.в. макрушин, в.а. малекова
машинное обучение на графах
рабочая программа дисциплины
для студентов, обучающихся по направлению подготовки
01.04.02   прикладная математика и информатика,
направленность программы:
«машинное обучение на текстах и графах»
рекомендовано ученым советом  факультета информационных технологий и анализа больших данных
(протокол №27 от 15.12.2022 г.)
одобрено советом учебно научного
департамента анализа данных и машинного обучения
(протокол №6 от 13.12.2022 г.)
москва 2023

['01.04.02', 'прикладная математика и информатика']


2) Документ — Интерактивные ТСКП, 2022.docx

кублик е. и.
интерактивные технологии современных коммуникационных платформ
рабочая программа дисциплины
для студентов, обучающихся
по направлению подготовки 45.03.02  лингвистика,
оп «когнитивная лингвистика и межкультурная коммуникация»,
профиль: «

In [153]:
tituls_2023[:10]

[{'МО на графах, МО на ТиГ, 2023.docx': ['01.04.02',
   'прикладная математика и информатика']},
 {'Интерактивные ТСКП, 2022.docx': ['45.03.02', 'лингвистика']},
 {'Технологии ОиАБД, Эк, 2022.docx': ['38.03.01', 'экономика']},
 {'Основы СА, ПИ, DO-И, 2023.docx': ['09.04.03', 'прикладная информатика']},
 {'Управление КПС, 2021.docx': ['09.03.03', 'прикладная информатика']},
 {'Инстр Power BI и Excel в лог, 2022.docx': ['38.03.02', 'менеджмент']},
 {'Программ на яз Python  и SQL, 2022.docx': ['38.03.01', 'экономика']},
 {'Визуализация данных, 2021, 2022.docx': ['38.03.02', 'менеджмент']},
 {'Математика МТС, 2021.docx': ['01.03.02',
   'прикладная математика и информатика']},
 {'Веб - разработка, ПИ, 2022.docx': ['09.03.03', 'прикладная информатика']}]

In [154]:
count_napravs_2023 = preprocessor.agg_count_napravs_year(tituls_2023)
count_napravs_2023

{'информационная безопасность': [8,
  ['А и СД в яз Python, ИБ, 2023.docx',
   'Автомат БС, 2021, 2022.docx',
   'Автомат системы БУАиАвКО, 2021, 2022.docx',
   'Компьютерное МЭиФС, ИБ, 2023.docx',
   'Математика, ИБ, 2023.docx',
   'Прикладные ЗМО, ИБ, 2023.docx',
   'Фин универ, ИБ, 2023.docx',
   'Финтех, ИБ, 2023.docx']],
 'математика и компьютерные науки': [3,
  ['А и СД в яз Python, МиКН, 2023.docx',
   'Практик по программ, МиКН, 2023.docx',
   'Фин универ, МиКН, 2023.docx']],
 'лингвистика': [2,
  ['Интерактивные ТСКП, 2022.docx', 'Тех обеспеч ИАиДК, 2022.docx']],
 'бизнес информатика': [2,
  ['А и СД в яз Python, БИ, 2023.docx', 'Основы ТИВ, БИ, 2023.docx']],
 'экономика': [10,
  ['А и СД в яз Python, Эк, 2023.docx',
   'Дискрет матем, Эк, 2023.docx',
   'Компьютерное МФО, Эк, 2022.docx',
   'МО и ИИ в бизнесе (на англ яз), 2022.docx',
   'Предиктивная АБД, 2022.docx',
   'Прикладные ЗМО и ОБД, Эк, 2023.docx',
   'Программ на VBA, 2021.docx',
   'Программ на яз Python  и SQL, 

In [155]:
not_others = ['Введение в НоД, ПИ, 2023.docx', 'Комп графика, 2021.docx', 'Корпоративный АД (SQL Server Analysis Services), 2022.docx', 'Методы ВД, ПИ, 2023.docx', 'ОТ на ест языках, ПИ,  2022.docx', 'Рекоменд СиКФ, ПИ, 2023.docx', 'Семантические тех, ПИ, 2023.docx', 'Технологии АДиМО, 2021.docx', 'Экология данных,  2022.docx', 'Авт пр на базе Power Automate, 2022.docx', 'Админ РСУБД (MS SQL),  2022.docx', 'Большие данные и МО,2021 г.п..docx', 'Большие данные и МОвСС, ПИ, 2021.docx', 'Корпоративное ОД (DataLake), 2022.docx', 'ОБД в экосистеме Hadoop,2022.docx', 'Обработка данных и МвТР, ПИ, 2023.docx', 'Прикладные ЗМО и ОБД, ПИ, 2023.docx', 'Применение НБД  при ОБД, 2022.docx', 'Технологии работы с ОД, ПИ, 2023.docx', 'Алг и анализ, ПИ, 2023.docx', 'Дискрет матем, ПИ, 2023.docx', 'Методы оптимизации, ПИ, 2021, 2022.docx', 'Основы ЧМ, ПИ, 2023.docx', 'Разработка ЭВА, ПИ, 2023.docx', 'Теория ОУ,2021.docx', 'Технологии и ААСМ, ПИ, 2023.docx', 'Инновационные ИТ, 2021.docx', 'Интеллектуальный АБИ, 2022.docx', 'МО в СиСА, ПИ, 2023.docx', 'Машинное зрение, ПИ, 2023.docx', 'Нейронные сети, 2021.docx', 'Опт задачи в МО, ПИ, 2023.docx', 'Основы ГО, ПИ, 2022.docx', 'Основы МЗ, ПИ, 2023.docx', 'Прикладные ЗМО, ПИ, 2023.docx', 'Современные НТ, 2021.docx', 'Web-программ, ПИ, 2023.docx', 'А и СД в яз Python, ПИ, 2023.docx', 'Объектно-ОП, ПИ, 2022.docx', 'Основы ВР, ПИ, 2023.docx', 'Основы МР, ПИ, 2023.docx', 'Паралл программ, 2021.docx', 'Программ на Haskell, 2021.docx', 'Программ для ВС, ПИ, 2023.docx', 'Современные ТП, 2022.docx', 'Технологии ПП, ПИ, 2023.docx', 'Низкоуров программ,2021, 2022.docx', 'Организация ВС, ПИ, 2023.docx', 'Основы СА, ПИ, DO-И, 2023.docx', 'ИТ-инфр предпр, 2022.docx', 'Компьютерное МЭиФС, ПИ, DO-И, 2023.docx', 'Моделирование БП, 2022.docx', 'Основы ММ, ПИ, 2023.docx', 'Основы ПИС, ПИ, 2023.docx', 'Проектирование ИС, ПИ, 2023.docx', 'Проектирование ИС, ПИИ, 2023.docx', 'Веб - разработка, ПИ, 2022.docx', 'Кроссплат разработка,  2021.docx', 'Методология программ, 2021.docx', 'Методы трансляции, ПИ, 2023.docx', 'Мобильная разработка, ПИ,  2021.docx', 'Операции разработки, 2021.docx', 'Высокопр выч, 2021.docx', 'Практик по программ, ПИ, 2023.docx', 'РБП на основе Power Apps, 2022.docx', 'РП в системе 1С Предпр, ПИ, 2023.docx', 'Разработка КиОП, 2021, 2022.docx', 'РУиАП в системе 1С Предпр,  2021.docx', 'Технологии РПдля МУ,  2021.docx', 'Архитектура и ДПО, ПИ, 2023.docx', 'Архитектура КС, 2021.docx', 'ИС на основе ИТ, 2021.docx', 'Корпоративные ИС, 2022.docx', 'Основы КИС, ПИ, 2023.docx', 'Метавыч и их прил, ПИ, 2023.docx', 'Управление КПС, 2021.docx', 'Бухгалтерские ИС, ПИ,  2021.docx', 'Основы БИС, ПИ, 2023.docx', 'Теор основы ФТ, ПИ, 2023.docx', 'У-А системы, 2022.docx', 'Финтех, DO-инж, 2023.docx', 'Финтех, ПИ, 2023.docx', 'Финтех, ПИ, DO-инж, 2023.docx']

[elem for elem in count_napravs_2023['прикладная информатика'][1] if elem not in not_others]

['Введение в спец, ПИ, 2023.docx',
 'Микр архитектура, ПИ, 2023.docx',
 'Основы ТИВ, ПИ, 2023.docx',
 'Планирование и ОПП, 2022.docx',
 'Системное и ППО, 2021.docx',
 'Системы УВ, ПИ, DO-И, 2023.docx',
 'Теория алгоритмов, 2022.docx',
 'Тестирование ПО, ПИ, 2023.docx']

In [156]:
[(elem, elem in count_napravs_2023['прикладная информатика'][1]) for elem in not_others]

[('Введение в НоД, ПИ, 2023.docx', True),
 ('Комп графика, 2021.docx', True),
 ('Корпоративный АД (SQL Server Analysis Services), 2022.docx', True),
 ('Методы ВД, ПИ, 2023.docx', True),
 ('ОТ на ест языках, ПИ,  2022.docx', True),
 ('Рекоменд СиКФ, ПИ, 2023.docx', True),
 ('Семантические тех, ПИ, 2023.docx', True),
 ('Технологии АДиМО, 2021.docx', True),
 ('Экология данных,  2022.docx', True),
 ('Авт пр на базе Power Automate, 2022.docx', True),
 ('Админ РСУБД (MS SQL),  2022.docx', True),
 ('Большие данные и МО,2021 г.п..docx', True),
 ('Большие данные и МОвСС, ПИ, 2021.docx', True),
 ('Корпоративное ОД (DataLake), 2022.docx', True),
 ('ОБД в экосистеме Hadoop,2022.docx', True),
 ('Обработка данных и МвТР, ПИ, 2023.docx', True),
 ('Прикладные ЗМО и ОБД, ПИ, 2023.docx', True),
 ('Применение НБД  при ОБД, 2022.docx', True),
 ('Технологии работы с ОД, ПИ, 2023.docx', True),
 ('Алг и анализ, ПИ, 2023.docx', True),
 ('Дискрет матем, ПИ, 2023.docx', True),
 ('Методы оптимизации, ПИ, 2021, 

Клавиатура для 2023 года:
- БИ (2)
- ИБ (8)
- Инноватика (4)
- Лингвистика (2)
- Менеджмент (11)
  - Аналитика (7)
    - Веб аналитика, 2021, 2022.docx
    - Визуализация данных, 2021, 2022.docx
    - Инстр Power BI и Excel в лог, 2022.docx
    - Инстр Power BI и Excel, 2021.docx
    - Основы БД и логистики, 2021, 2022.docx
    - П и АД с пом Python, Мен, 2021, 2022.docx
    - Прикл стат в логистике, 2021, 2022.docx
  - Прочие (4)
- МехиРоб (3)
- МКН (3)
- ПИ (91)
  - Аналитика (9)
    - Введение в НоД, ПИ, 2023.docx
    - Комп графика, 2021.docx
    - Корпоративный АД (SQL Server Analysis Services), 2022.docx
    - Методы ВД, ПИ, 2023.docx
    - ОТ на ест языках, ПИ,  2022.docx
    - Рекоменд СиКФ, ПИ, 2023.docx
    - Семантические тех, ПИ, 2023.docx
    - Технологии АДиМО, 2021.docx
    - Экология данных,  2022.docx
  - Большие данные (10)
    - Авт пр на базе Power Automate, 2022.docx
    - Админ РСУБД (MS SQL),  2022.docx
    - Большие данные и МО,2021 г.п..docx
    - Большие данные и МОвСС, ПИ, 2021.docx
    - Корпоративное ОД (DataLake), 2022.docx
    - ОБД в экосистеме Hadoop,2022.docx
    - Обработка данных и МвТР, ПИ, 2023.docx
    - Прикладные ЗМО и ОБД, ПИ, 2023.docx
    - Применение НБД  при ОБД, 2022.docx
    - Технологии работы с ОД, ПИ, 2023.docx
  - Математика (7)
    - Алг и анализ, ПИ, 2023.docx
    - Дискрет матем, ПИ, 2023.docx
    - Методы оптимизации, ПИ, 2021, 2022.docx
    - Основы ЧМ, ПИ, 2023.docx
    - Разработка ЭВА, ПИ, 2023.docx
    - Теория ОУ,2021.docx
    - Технологии и ААСМ, ПИ, 2023.docx
  - Машинное обучение (10)
    - Инновационные ИТ, 2021.docx
    - Интеллектуальный АБИ, 2022.docx
    - МО в СиСА, ПИ, 2023.docx
    - Машинное зрение, ПИ, 2023.docx
    - Нейронные сети, 2021.docx
    - Опт задачи в МО, ПИ, 2023.docx
    - Основы ГО, ПИ, 2022.docx
    - Основы МЗ, ПИ, 2023.docx
    - Прикладные ЗМО, ПИ, 2023.docx
    - Современные НТ, 2021.docx
  - Программирование (10)
    - Web-программ, ПИ, 2023.docx
    - А и СД в яз Python, ПИ, 2023.docx
    - Объектно-ОП, ПИ, 2022.docx
    - Основы ВР, ПИ, 2023.docx
    - Основы МР, ПИ, 2023.docx
    - Паралл программ, 2021.docx
    - Программ на Haskell, 2021.docx
    - Программ для ВС, ПИ, 2023.docx
    - Современные ТП, 2022.docx
    - Технологии ПП, ПИ, 2023.docx
  - Разработка (30)
    - АО (3)
      - Низкоуров программ,2021, 2022.docx
      - Организация ВС, ПИ, 2023.docx
      - Основы СА, ПИ, DO-И, 2023.docx
    - Моделирование (7)
      - ИТ-инфр предпр, 2022.docx
      - Компьютерное МЭиФС, ПИ, DO-И, 2023.docx
      - Моделирование БП, 2022.docx
      - Основы ММ, ПИ, 2023.docx
      - Основы ПИС, ПИ, 2023.docx
      - Проектирование ИС, ПИ, 2023.docx
      - Проектирование ИС, ПИИ, 2023.docx
    - ПО (6)
      - Веб - разработка, ПИ, 2022.docx
      - Кроссплат разработка,  2021.docx
      - Методология программ, 2021.docx
      - Методы трансляции, ПИ, 2023.docx
      - Мобильная разработка, ПИ,  2021.docx
      - Операции разработки, 2021.docx
    - Приложения (7)
      - Высокопр выч, 2021.docx
      - Практик по программ, ПИ, 2023.docx
      - РБП на основе Power Apps, 2022.docx
      - РП в системе 1С Предпр, ПИ, 2023.docx
      - Разработка КиОП, 2021, 2022.docx
      - РУиАП в системе 1С Предпр,  2021.docx
      - Технологии РПдля МУ,  2021.docx
    - Системы (5)
      - Архитектура и ДПО, ПИ, 2023.docx
      - Архитектура КС, 2021.docx
      - ИС на основе ИТ, 2021.docx
      - Корпоративные ИС, 2022.docx
      - Основы КИС, ПИ, 2023.docx
    - Тестирование (2)
      - Метавыч и их прил, ПИ, 2023.docx
      - Управление КПС, 2021.docx
  - Финтех (7)
    - Бухгалтерские ИС, ПИ,  2021.docx
    - Основы БИС, ПИ, 2023.docx
    - Теор основы ФТ, ПИ, 2023.docx
    - У-А системы, 2022.docx
    - Финтех, DO-инж, 2023.docx
    - Финтех, ПИ, 2023.docx
    - Финтех, ПИ, DO-инж, 2023.docx
  - Прочие (8)
- ПИнж (7)
- ПМИ (42)
  - Аналитика (8)
    - Введение в НоД, ПМИ, 2023.docx
    - Метавыч и их прил, ПМИ, 2023.docx
    - Методы ВД, ПМИ, 2023.docx
    - Рекоменд СиКФ, ПМИ, 2023.docx
    - Семантические тех, ПМИ, 2023.docx
    - Технологии ММиАД ,  2021.docx
    - Технологии ОБД, ПМИ, 2023.docx
    - Технологии работы с ОД, ПМИ, 2023.docx
  - Математика (9)
    - Имитационное и АМ, ПМИ, 2021.docx
    - Математика МТС, 2021.docx
    - Модели ЦД, 2021.docx
    - Основы ММ, ПМИ, 2023.docx
    - Основы ЧМ, ПМИ, 2023.docx
    - Прикладная ТГ, 2021.docx
    - Разработка ЭВА, ПМИ, 2023.docx
    - Стохастическая ФМ, 2021.docx
    - Технологии и ААСМ, ПМИ, 2023.docx
  - Машинное обучение (6)
    - МО в СиСА, ПМИ, 2023.docx
    - МО в трейдинге,  2021.docx
    - МО на графах, МО на ТиГ, 2023.docx
    - Машинное зрение, ПМИ, 2023.docx
    - Опт задачи в МО, ПМИ, 2023.docx
    - Прикладные ЗМО, ПМИ, 2023.docx
  - Разработка (10)
    - Архитектура и ДПО, ПМИ, 2023.docx
    - Методы трансляции, ПМИ, 2023.docx
    - Микр архитектура, ПМИ, 2023.docx
    - Основы БИС, ПМИ, 2023.docx
    - Основы ВР, ПМИ, 2023.docx
    - Основы КИС, ПМИ, 2023.docx
    - Основы МР, ПМИ, 2023.docx
    - Основы ПИС, ПМИ, 2023.docx
    - Тестирование ПО, ПМИ, 2023.docx
    - Технологии ПП, ПМИ, 2023.docx
  - Прочие (9)
- Экономика (10)
  - Аналитика (5)
    - Предиктивная АБД, 2022.docx
    - Прикладные ЗМО и ОБД, Эк, 2023.docx
    - Программ на яз Python  и SQL, 2022.docx
    - Современные ТППиОД , 2021, 2022.docx
    - Технологии ОиАБД, Эк, 2022.docx
  - Прочие (5)

##### Генерация сообщений к дисциплинам

Общий вид структуры данных дисциплин и краткой аналитической сводки по ним:
- CSV файл
  - 1 столбец - наименование файла РПД дисциплины
  - 2 столбец — ключевые слова
  - 3 столбец — ключевые сочетания из 2 слов
  - 4 столбец — ключевые сочетания из 3 слов
  - 5 столбец — название дисциплины (как в полученном от парсера финальном датасете)
  - 6 столбец — аналитическая сводка по этой дисциплине

Общий вид сообщения от бота по конкретной дисциплине, которое хранится в табличке

1. Название дисциплины (берём из словаря file_to_name_rpd)
2. Направление подготовки и его код (парсим с титульника РПД)
3. Ступень образования (парсим с титульника РПД)
4. Направленность программы (парсим с титульника РПД)
5. Охватываемые темы дисциплины (парсим ранее с таблички в пункте 5.2 РПД на общем датасете)
6. Самые частые слова (берём результат работы NLP модели)
7. Ссылка на РПД (берём из словаря file_to_name_rpd)

###### Название дисциплины, тем. план и ссылка

In [ ]:
file_to_name_rpd = {}
file_to_name_rpd.update(files_rpd_names_2021)
file_to_name_rpd.update(files_rpd_names_2022)
file_to_name_rpd.update(files_rpd_names_2023)

In [ ]:
dict(list(file_to_name_rpd.items())[:5])

{'Инт вещей, ПИ, 2021.docx': {'NAME': 'Интернет вещей',
  'THEMES': ['Введение в «интернет вещей»',
   'Архитектура и безопасность решений «интернета вещей»',
   'Аппаратное обеспечение «интернета вещей»',
   'Программное обеспечение «интернета вещей»',
   'Реализация проектов «интернета вещей»'],
  'LINKDOC': 'vk.cc/cvqvu3'},
 'Агент мод.docx': {'NAME': 'Агентное моделирование',
  'THEMES': ['Основы агентно-ориентированного и имитационного моделирования',
   'Моделирование случайных величин',
   'Агентно-ориентированное моделирование',
   'Обработка и интерпретация результатов агентно-ориентированного моделирования построение моделей'],
  'LINKDOC': 'vk.cc/cvqvu0'},
 'Интел тех в УР.docx': {'NAME': 'Интеллектуальные технологии в управлении рисками',
  'THEMES': ['Понятия риска, методы управления, учета, классификация математический аппарат, необходимый для построения современных моделей риск-менеджмента',
   'Нейросетевые модели прогнозирования обзор современных алгоритмов построение

###### Направление подготовки

In [ ]:
file_to_naprav_rpd = {namefile: naprav for namefile, naprav in [list(titul.items())[0] for titul in tituls_2021]}

file_to_naprav_rpd.update({namefile: naprav for namefile, naprav in [list(titul.items())[0] for titul in tituls_2022]})
file_to_naprav_rpd.update({namefile: naprav for namefile, naprav in [list(titul.items())[0] for titul in tituls_2023]})

dict(list(file_to_naprav_rpd.items())[:15])

{'Инт вещей, ПИ, 2021.docx': ['09.04.03', 'прикладная информатика'],
 'Агент мод.docx': ['09.06.01', 'информатика и вычислительная техника'],
 'Интел тех в УР.docx': ['01.04.02', 'прикладная математика и информатика'],
 'Соврем НТ, 2021.docx': ['01.04.02', 'прикладная математика и информатика'],
 'Бухгалтерские ИС.docx': ['01.03.02', 'прикладная математика и информатика'],
 'Диф урав.docx': ['01.03.02', 'прикладная математика и информатика'],
 'Метод ПИДиПДДА.docx': ['01.04.02', 'прикладная математика и информатика'],
 'АС БУ АиА в КО.docx': ['09.04.03', 'прикладная информатика'],
 'Прогр на яз Python и SQL, Эк.docx': ['38.04.01', 'экономика'],
 'СоврТП, ПИ.docx': ['09.03.03', 'прикладная информатика'],
 'Прогр и АД с пом PYTHON, Ин.docx': ['27.03.05', 'инноватика'],
 'Реком системы.docx': ['01.04.02', 'прикладная математика и информатика'],
 'Прикл задачи МОиОБД, Эк.docx': ['38.04.01', 'экономика'],
 'Прикл мод и МТСС.docx': ['01.04.02', 'прикладная математика и информатика'],
 'А-О 

###### Ступень образования и направленность программы

In [ ]:
graduates = dict()

print("Титульные страницы РПД:")
print()
for ind, filee in enumerate(files_2021+files_2022+files_2023):
  if filee in files_2021:
    doc = docx.Document(docs_2021_path + filee)
    now_count_napravs = count_napravs_2021
  elif filee in files_2022:
    doc = docx.Document(docs_2022_path + filee)
    now_count_napravs = count_napravs_2022
  elif filee in files_2023:
    doc = docx.Document(docs_2023_path + filee)
    now_count_napravs = count_napravs_2023
  print()
  print(f'{ind+1}) Документ — {filee}')
  print()
  print(*[re.sub('[^A-Za-zА-Яа-я]+', ' ', p.text.lower()).strip() for p in doc.paragraphs[8:45] if re.sub('[^A-Za-zА-Яа-я]+', ' ', p.text.lower()).strip() not in ('', ' ')], sep='\n')
  titul = [re.sub('[^A-Za-zА-Яа-я]+', ' ', p.text.lower()).strip() for p in doc.paragraphs[8:45] if re.sub('[^A-Za-zА-Яа-я]+', ' ', p.text.lower()).strip() not in ('', ' ')]
  for ind, data in enumerate(titul):
    if ((data.startswith('оп')) or (data.startswith('образовательная программа')) or (data.startswith('направленност')) or (data.startswith('профиль')) or (data.startswith('научная специальность'))):
      key_ind = ind
    elif data.startswith('москва') or data.startswith('рекомендовано ученым'):
      end_ind = ind
      break
    elif 'оп' in data:
      if data.split()[0] in now_count_napravs and data.split()[1] == 'оп':
        key_ind = ind
      elif data.startswith('для студентов обучающихся по направлению подготовки'):
        if data.split()[6] in now_count_napravs and data.split()[7] == 'оп':
          key_ind = ind
  titul = titul[key_ind:end_ind]

  if 'магистратуры' in titul[0]:
    graduate = 'Магистратура'
    titul = ' '.join(titul[1:]) if titul[-1].startswith('в') else ', '.join(titul[1:])
  elif 'аспирантуре' in titul[-1]:
    graduate = 'Аспирантура'
    if titul[0] == 'направленность программы':
      if len(titul) > 3:
        titul = ' '.join(titul[1:-1]) if titul[-2].startswith('и') else ', '.join(titul[1:-1])
      else:
        titul = titul[1]
    elif len(titul[0]) > len('направленность программы') and 'направленность программы' in titul[0]:
      titul = titul[0][len('направленность программы')+1:] if len(titul) == 2 else ', '.join([titul[0][len('направленность программы')+1:]] + titul[1:-1])
    else:
      if len(titul) == 2:
        titul = ', '.join(titul[:-1])
      else:
        titul = titul[0]
  else:
    graduate = 'Бакалавриат'
    if titul[0].startswith('оп'):
      if titul[0][3:] in now_count_napravs.keys():
        if len(titul) == 1:
          titul = titul[0][3:]
        else:
          titul = ', '.join(titul[1:])
      else:
        titul = titul[0][3:]
    elif titul[0].startswith('образовательная программа'):
      if titul[0][26:] in now_count_napravs.keys():
        titul = ', '.join(titul[1:])
      else:
        titul = titul[0][26:]
    elif titul[0].startswith('профиль'):
      if len(titul) == 1:
        titul = titul[0][8:]
      elif len(titul) > 1:
        titul = ' '.join([titul[0][8:]] + titul[1:]) if titul[1].startswith('в') else ', '.join([titul[0][8:]] + titul[1:])

    elif titul[0].startswith('направленност'):
      if titul[0] == 'направленность программы' or titul[0] == 'направленности программы':
        if len(titul) > 2:
          titul = ' '.join(titul[1:]) if titul[-2].startswith('и') else ', '.join(titul[1:])
        else:
          titul = titul[1]
      elif len(titul[0]) > len('направленность программы') and 'направленность программы' in titul[0]:
        titul = titul[0][len('направленность программы')+1:] if len(titul) == 2 else ', '.join([titul[0][len('направленность программы')+1:]] + titul[1:-1])

    elif titul[0].split()[0] in now_count_napravs and titul[0].split()[1] == 'оп':
      titul = ' '.join(titul[0].split()[2:])

    elif titul[0] == 'для всех образовательных программ':
      titul = 'общая'

    elif titul[0].split()[6] in now_count_napravs and titul[0].split()[7] == 'оп':
      titul = ' '.join(titul[0].split()[8:])

    elif 'оп' in titul[-1]:
      titul = ', '.join(titul[:-1])

  print()
  print('======================')
  print(*[[titul], graduate], sep='\n')
  print('======================')
  print()
  graduates[filee] = [titul.capitalize(), graduate]

Выходные данные были обрезаны до нескольких последних строк (5000).
место дисциплины в структуре образовательной программы
объем дисциплины модуля в зачетных единицах и в академических часах с выделением объема аудиторной лекции семинары и самостоятельной работы обучающихся
содержание дисциплины структурированное по темам разделам дисциплины с указанием их объемов в академических часах и видов учебных занятий
содержание дисциплины
учебно тематический план
содержание семинаров практических занятий
перечень учебно методического обеспечения для самостоятельной работы обучающихся по дисциплине
перечень вопросов отводимых на самостоятельное освоение дисциплины формы внеаудиторной самостоятельной работы

['управление бизнесом профиль менеджмент в спорте']
Бакалавриат


245) Документ — Основы ГО, ПИ, 2022.docx

утверждаю
проректор по учебной и методической работе
е а каменева
г
с в макрушин з х калажоков
оcновы глубокого обучения
рабочая программа дисциплины
для студентов обучающихся по напра

In [ ]:
graduates

{'Инт вещей, ПИ, 2021.docx': ['Обработка больших данных и разработка интеллектуальных приложений',
  'Магистратура'],
 'Агент мод.docx': ['Математическое моделирование, численные методы и комплексы программ',
  'Аспирантура'],
 'Интел тех в УР.docx': ['Анализ больших данных и машинное обучение в экономике и финансах',
  'Магистратура'],
 'Соврем НТ, 2021.docx': ['Анализ больших данных и машинное обучение в экономике и финансах',
  'Магистратура'],
 'Бухгалтерские ИС.docx': ['Анализ данных и принятие решений в экономике и финансах',
  'Бакалавриат'],
 'Диф урав.docx': ['Анализ данных и принятие решений в экономике и финансах',
  'Бакалавриат'],
 'Метод ПИДиПДДА.docx': ['Анализ больших данных и машинное обучение в экономике и финансах',
  'Магистратура'],
 'АС БУ АиА в КО.docx': ['Обработка больших данных и разработка интеллектуальных приложений',
  'Магистратура'],
 'Прогр на яз Python и SQL, Эк.docx': ['Корпоративные финансы и управление, финансовый анализ и оценка инвестиционных реше

###### Самые частые слова

In [ ]:
PATH = '/content/gdrive/MyDrive/Диплом_Валяев/data'
docs_rpd_keywords = PATH+'/rpd_keywords_ngramms.json'

with open(docs_rpd_keywords, 'r', encoding='utf-8') as file:
  rpd_keywords = json.load(file)

dict(list(rpd_keywords.items())[:10])

{'Прикл задачи МОиОБД, Эк, КФУ.docx': {'keywords': ['spark',
   'hadoop',
   'кластер',
   'pandas',
   'yarn'],
  'twogramms': ['структура кластер',
   'hadoop принцип',
   'кластер yarn',
   'машинный обучение',
   'кластер hdinsight'],
  'threegramms': ['библиотека pandas объект',
   'learn решение машинный',
   'решение машинный обучение',
   'scikit learn решение',
   'выявлять различный метод'],
  'name': 'прикладные задачи машинного обучения и обработки больших данных 2020'},
 'Методы ВД,Эк,КФУ.docx': {'keywords': ['диаграмма',
   'гистограмма',
   'визуальный',
   'линейчатый',
   'microsoft'],
  'twogramms': ['линейчатый диаграмма',
   'визуальный элемент',
   'microsoft power',
   'power bi',
   'microsoft excel'],
  'threegramms': ['microsoft power bi',
   'линейный гистограмма гистограмма',
   'накопление линейный гистограмма',
   'формирование отчет сводный',
   'банка фильтрация формирование'],
  'name': 'методы визуализации данных 2020'},
 'Програм. на языках PYTHON и SQ

###### Общий сбор всех материалов по всем РПД

- `file_to_name_rpd` — основа общего сбора данных (название дисциплины, тематический план и ссылка на документ)
- `file_to_naprav_rpd` — направление подготовки и его код
- `graduates` — ступень образования + направленность программы
- `rpd_keywords` — самые частые слова + биграммы и триграммы

In [ ]:
for file_rpd in file_to_name_rpd.keys():
  file_to_name_rpd[file_rpd]["DIRECTION"] = f'{file_to_naprav_rpd[file_rpd][0]}, «{file_to_naprav_rpd[file_rpd][1].capitalize()}»'
  file_to_name_rpd[file_rpd]["LEVEL"] = graduates[file_rpd][1]
  file_to_name_rpd[file_rpd]["FOCUS"] =  graduates[file_rpd][0]
  file_to_name_rpd[file_rpd]["THREEGRAMMS"] = rpd_keywords[file_rpd]['threegramms']
  file_to_name_rpd[file_rpd]["TWOGRAMMS"] = rpd_keywords[file_rpd]['twogramms']
  file_to_name_rpd[file_rpd]["KEYWORDS"] = rpd_keywords[file_rpd]['keywords']

file_to_name_rpd

{'Инт вещей, ПИ, 2021.docx': {'NAME': 'Интернет вещей',
  'THEMES': ['Введение в «интернет вещей»',
   'Архитектура и безопасность решений «интернета вещей»',
   'Аппаратное обеспечение «интернета вещей»',
   'Программное обеспечение «интернета вещей»',
   'Реализация проектов «интернета вещей»'],
  'LINKDOC': 'vk.cc/cvqvu3',
  'DIRECTION': '09.04.03, «Прикладная информатика»',
  'LEVEL': 'Магистратура',
  'FOCUS': 'Обработка больших данных и разработка интеллектуальных приложений',
  'THREEGRAMMS': ['архитектура интернет вещь',
   'интернет вещь использование',
   'обеспечение интернет вещь',
   'интернет вещь архитектура',
   'тренд область интернет'],
  'TWOGRAMMS': ['интернет вещь',
   'архитектура интернет',
   'вещь использование',
   'обеспечение интернет',
   'плата arduino'],
  'KEYWORDS': ['вещь', 'интернет', 'arduino', 'плк', 'проект']},
 'Агент мод.docx': {'NAME': 'Агентное моделирование',
  'THEMES': ['Основы агентно-ориентированного и имитационного моделирования',
   'Мо

###### Создание сообщений

Структура данных для создания сообщений выглядит следующим образом:
- Файл РПД
  - Ключ «NAME» — название дисциплины
  - Ключ «THEMES» — охватываемые темы дисциплины
  - Ключ «LINKDOC» — ссылка на файл РПД дисциплины
  - Ключ «DIRECTION» — направление подготовки дисциплины и его код
  - Ключ «LEVEL» — ступень образования дисциплины
  - Ключ «FOCUS» — направленность программы
  - Ключ «THREEGRAMMS» — самые частые сочетания из 3 слов в дисциплине
  - Ключ «TWOGRAMMS» — самые частые сочетания из 2 слов в дисциплине
  - Ключ «KEYWORDS» — самые частые слова в дисциплине

Шаблон сообщения к дисциплине от бота:
<br>
<br>
<hr>

Дисциплина: «{ключ «NAME»}»

Направление подготовки: {ключ «DIRECTION»}

Ступень: {ключ «LEVEL»}

Направленность программы: «{ключ «FOCUS»}»

Примерные темы:

{ключ «THEMES»}

Самые частые слова: {ключ «KEYWORDS»}

Подробнее изучить дисциплину можно по следующей ссылке: {ключ «LINKDOC»}.
<hr>

In [ ]:
print('Аналитическая сводка по РПД для бота:')
print()
rpd_msg_bot = []
for ind, file_rpd in enumerate(list(file_to_name_rpd.keys())):
  themes = '.\n'.join(file_to_name_rpd[file_rpd]["THEMES"])
  keywords = ', '.join([f'«{word}»' for word in file_to_name_rpd[file_rpd]['KEYWORDS']])

  msg = f'Дисциплина: «{file_to_name_rpd[file_rpd]["NAME"]}».\n'
  msg += f'Направление подготовки: {file_to_name_rpd[file_rpd]["DIRECTION"]}.\n'
  msg += f'Ступень: {file_to_name_rpd[file_rpd]["LEVEL"]}.\n'
  msg += f'Направленность программы: «{file_to_name_rpd[file_rpd]["FOCUS"]}».\n\n'
  msg += f'Примерные темы:\n{themes}.\n\n'
  msg += f'Самые частые слова: {keywords}.\n\n'
  msg += f'Подробнее изучить дисциплину можно по следующей ссылке: {file_to_name_rpd[file_rpd]["LINKDOC"]}.'

  print(f'{ind+1}) Документ — {file_rpd}')
  print()
  print(msg)
  print()
  print()

  rpd_msg_bot.append([file_rpd, ', '.join(file_to_name_rpd[file_rpd]["KEYWORDS"]), ', '.join(file_to_name_rpd[file_rpd]["TWOGRAMMS"]), ', '.join(file_to_name_rpd[file_rpd]["THREEGRAMMS"]), file_to_name_rpd[file_rpd]["NAME"], msg])

Выходные данные были обрезаны до нескольких последних строк (5000).
Примерные темы:
Введение в искусственные нейронные сети и глубокое обучение.
Обучение искусственных нейронных сетей.
Сверточные искусственные нейронные сети.
Представление объектов в виде векторов малой размерности.
Рекуррентные нейронные сети.
Механизм внимания для искусственных нейронных сетей.
Обучение с подкреплением.
Графовые нейронные сети.

Самые частые слова: «pytorch», «сеть», «нейронный», «инс», «сверточный».

Подробнее изучить дисциплину можно по следующей ссылке: vk.cc/cvqvjv.


166) Документ — Глубокое обучение, ПИ, 2022.docx

Дисциплина: «Глубокое обучение пи».
Направление подготовки: 09.03.03, «Прикладная информатика».
Ступень: Бакалавриат.
Направленность программы: «Ит сервисы и технологии обработки данных в экономике и финансах, высокопроизводительные вычисления в цифровой экономике».

Примерные темы:
Введение в искусственные нейронные сети и глубокое обучение.
Обучение искусственных нейронных сетей.
С

##### Конечная выгрузка в табличку

In [ ]:
faq_table_df = pd.DataFrame(rpd_msg_bot, columns=['Файл', 'Юзер сейс', 'Биграммы', 'Триграммы', 'Название', 'Сообщение'])
faq_table_df

Файл  \
0            Инт вещей, ПИ, 2021.docx   
1                       Агент мод.docx   
2                  Интел тех в УР.docx   
3                 Соврем НТ, 2021.docx   
4                Бухгалтерские ИС.docx   
..                                 ...   
396     Теор основы ФТ, ПМИ, 2023.docx   
397  Проектирование ИС, ПИИ, 2023.docx   
398   Проектирование ИС, ПИ, 2023.docx   
399        Предиктивная АБД, 2022.docx   
400    Системы УВ, ПИ, DO-И, 2023.docx   

                                             Юзер сейс  \
0                 вещь, интернет, arduino, плк, проект   
1    моделирование, агентный, имитационный, случайн...   
2    риск, имитационный, построение, нечеткий, нечетко   
3           сеть, нейронный, нейрон, персептрон, keras   
4       бухгалтерский, учет, счет, информационный, ндс   
..                                                 ...   
396   блокчейн, цифровой, платформа, мобильный, платеж   
397  проектирование, информационный, жизненный, раз...   
398  жизненный, проектирование, информационный, про...   
399  когнитивный, предиктивный, аналитика, бизнес, ...   
400             git, версия, ветка, gitlab, управление   

                                              Биграммы  \
0    интернет вещь, архитектура интернет, вещь испо...   
1    агентный ориентировать, случайный величина, ор...   
2    построение имитационный, управление риск, учет...   
3    нейронный сеть, функция активация, персептрон ...   
4    бухгалтерский учет, информационный бухгалтерск...   
..                                                 ...   
396  цифровой платформа, финансовый технология, бло...   
397  проектирование информационный, разрабатывать п...   
398  цикл информационный, жизненный цикл, case сред...   
399  предиктивный аналитика, использование python, ...   
400  управление версия, характеристика управление, ...   

                                             Триграммы  \
0    архитектура интернет вещь, интернет вещь испол...   
1    агентный ориентировать моделирование, моделиро...   
2    построение имитационный анализ, имитационный а...   
3    нейронный сеть метод, метод градиентный спуск,...   
4    информационный бухгалтерский учет, счет бухгал...   
..                                                 ...   
396  мобильный операторский платежный, криптовалюта...   
397  разрабатывать пакет документ, пакет документ п...   
398  жизненный цикл информационный, стандартизация ...   
399  поддержка принятие решение, надежность заемщик...   
400  характеристика управление версия, разработка п...   

                                             Название  \
0                                      Интернет вещей   
1                              Агентное моделирование   
2    Интеллектуальные технологии в управлении рисками   
3                 Современные нейросетевые технологии   
4                Бухгалтерские информационные системы   
..                                                ...   
396    Теоретические основы финансовых технологий пми   
397          Проектирование информационных систем пии   
398           Проектирование информационных систем пи   
399             Предиктивная аналитика больших данных   
400                       Системы управления версиями   

                                             Сообщение  
0    Дисциплина: «Интернет вещей».\nНаправление под...  
1    Дисциплина: «Агентное моделирование».\nНаправл...  
2    Дисциплина: «Интеллектуальные технологии в упр...  
3    Дисциплина: «Современные нейросетевые технолог...  
4    Дисциплина: «Бухгалтерские информационные сист...  
..                                                 ...  
396  Дисциплина: «Теоретические основы финансовых т...  
397  Дисциплина: «Проектирование информационных сис...  
398  Дисциплина: «Проектирование информационных сис...  
399  Дисциплина: «Предиктивная аналитика больших да...  
400  Дисциплина: «Системы управления версиями».\nНа...  

[401 rows x 6 columns]

In [ ]:
try:
  faq_table_df.to_csv('/content/gdrive/MyDrive/Диплом_Валяев/data/rpd_msg_bot.csv', index=False)
  print('Загрузка датасета прошла успешно!\nСоздан файл «rpd_msg_bot.csv».')
except Exception as e:
  print('Ошибка:\n', traceback.format_exc())

Загрузка датасета прошла успешно!
Создан файл «rpd_msg_bot.csv».


## Сохранение результатов обработки

### Датасет корпусов текстов РПД

In [ ]:
try:
  with open("/content/gdrive/MyDrive/Диплом_Валяев/data/rpd_data.json", "w", encoding="utf-8") as file:
      json.dump(rpd_data, file, ensure_ascii=False, indent=4)
  print('Загрузка датасета прошла успешно!\nСоздан файл «rpd_data.json».')
except Exception as e:
  print('Ошибка:\n', traceback.format_exc())

Загрузка датасета прошла успешно!
Создан файл «rpd_data.json».


### Датасет индексов РПД и их файлов

In [ ]:
try:
  with open("/content/gdrive/MyDrive/Диплом_Валяев/data/name_to_file_rpd.json", "w", encoding="utf-8") as file:
      json.dump(name_to_file_rpd, file, ensure_ascii=False, indent=4)
  print('Загрузка датасета прошла успешно!\nСоздан файл «name_to_file_rpd.json».')
except Exception as e:
  print('Ошибка:\n', traceback.format_exc())

Загрузка датасета прошла успешно!
Создан файл «name_to_file_rpd.json».
